# Dynamic and Flexible Labeling with GPT Models for Text Classification

This GitHub repository holds the code and materials designed for a dynamic and innovative approach to text classification using GPT-4 and GPT-3.5 models. It introduces an iterative refinement process, initiating the classification with GPT-4 and progressively enhancing accuracy through human validation and model fine-tuning.

The original replication code can be found in the replication folder.

## Overview
### Iterative Refinement and Dynamic Labeling Process
This methodology is rooted in the iterative refinement and dynamic labeling process. It begins with GPT-4 undertaking the initial classification of a small sample of text. Human reviewers then validate this classification, ensuring accuracy. The validated data serves dual purposes - 1) If the classifications rendered by GPT-4 meet the established accuracy, the model can be applied to a larger sample for further validation and then to the entire dataset; 2) if the classification needs further refinement, the human-validated results will be used as dataset to fine-turn the GPT-3.5 model.
1. ##### Multi-Theme Classification
The code's versatility is underscored by its capacity for multi-theme classification. It’s equipped to dissect a text and concurrently classify it into multiple themes. 
2. ##### Multi-Verification
The GPTClassifier class, integral to this approach, is equipped with a multi_verify method. This method ensures the robustness of classifications by sending out multiple queries to the OpenAI API, retrieving a variety of results, and comparing them. 
##### Number of verification (once_verify_num)
OpenAI's pricing for classification tasks is based on the total number of tokens processed, including both the tokens in the questions and the answers. The cost of each classification is calculated as the sum of the tokens in the question and answer, multiplied by their respective prices per token. Retries are usually less cost-efficient than higher numbers of once_verify_num, as they re-incur the cost of question tokens.

To minimize costs, it is essential to strategically set the once_verify_num. This parameter should be adjusted based on the specific requirements and complexities of each classification task to avoid inconclusive results and reduce the need for costly retries. For example, in a one-theme, two-class variable classification task, setting an appropriate once_verify_num =3 helps prevent an equal number of responses for each class, thereby avoiding inconclusive results.


#### Dynamic Labeling
The dynamic labeling process significantly reduces the initial labeled data requirements. It begins the journey with a sample of 200 labeled posts, progressively adding more labeled data in iterations. Each addition refines the model's accuracy, ensuring that the classification becomes more precise with each step.

#### Iterative Refinement
Every iteration of classification and validation refines the model's understanding and accuracy. The process is flexible, adapting to the complexities and nuances of the text being classified. This adaptability ensures that the model is not static but is dynamic, learning, and evolving with each iteration.



## Authentication

To utilize this package, you need to access OpenAI's API, requiring an API key. Follow these steps to set it up:
1. Create an Account for OpenAI Platform (https://platform.openai.com/overview)
2. Click "View API Key" , then "Create new secret key"
3. Copy the key, and take note of the key as it will be needed to authenticate your requests.

In [ ]:
import os
import openai
openai.api_key = "YOUR-API-KEY"

## Installation

In [2]:
# load packages 
from gpt_classify_function import *
from sklearn.model_selection import train_test_split

## Annoate the task 
We can now go ahead and classify the texts.

In [3]:
# Set the Constants
SAMPLE_SIZE = 200 # the number of sample classfied and varified in each round 
SEED = 106
ACCEPTABLE_ACCURACY = 0.85

In [4]:
# Load the data
df = pd.read_excel("01_Immigrant Coding Training.xlsx")

# Convert to integer and then to string
cols_to_convert = ['Q1', 'Q2', 'Q3_1', 'Q3_2','Q3_3', 'Q3_4', 'Q3_5', 'Q3_6','Q3_7', 'Q3_8', 'Train']
for col in cols_to_convert:
    df[col] = df[col].astype(int).astype(str)

# Split train and test dataset 
train_df, test_df = train_test_split(df, test_size=0.5, random_state=SEED)
train_df.to_excel('02_train_df.xlsx', index=False)
test_df.to_excel('02_test_df.xlsx', index=False)
train_df

ID  ID_original                                  GUID  \
1833  1835         8457  64302c76-b8cb-4138-96f2-bc84c5a1400f   
358    359         1749  0e722094-d391-4582-82f7-9b2f75b359e1   
257    258         1223  9f8b44b3-4601-4f35-b89b-d440e98882b0   
835    836         4055  195199fc-5331-43f2-926e-853005ad6281   
1048  1049         4997  9c822d93-9b12-482c-acac-a48376712cbc   
...    ...          ...                                   ...   
447    448         2205  1a59076f-f646-4138-8f7c-b57dcca1b5f8   
1945  1947          246  67558aaa-c983-4b5b-bbc2-eb39555baa3c   
295    296         1475  60d489a3-b29c-4e27-8bc0-2048616a71e2   
986    987         4701  809292cc-15fe-4487-8b73-946c2fa66e38   
1390  1392         6460  018b5ed6-b779-47c7-a7e3-6b8f12f303df   

              Date (GMT)                                                URL  \
1833 2018-01-05 03:16:42  https://www.usatoday.com/story/news/politics/2...   
358  2018-01-11 05:00:00  https://www.yahoo.com/news/m/7e9bccdf-0493-353...   
257  2018-01-03 03:08:53  http://abcnews.go.com/international/wirestory/...   
835  2018-01-06 20:17:41  http://www.breitbart.com/news/the-latest-trump...   
1048 2018-01-06 19:21:57  http://thehill.com/homenews/senate/367759-sand...   
...                  ...                                                ...   
447  2018-01-08 17:02:11  https://www.yahoo.com/news/10-migrants-dead-do...   
1945 2018-02-07 01:29:17  http://thehill.com/homenews/senate/372658-mcco...   
295  2018-01-08 23:36:21  http://www.breitbart.com/news/pelosi-is-optimi...   
986  2018-01-02 08:10:01  https://www.nytimes.com/2018/01/02/world/asia/...   
1390 2018-01-10 22:12:39  http://www.cnn.com/transcripts/1801/10/wolf.01...   

                                             Post_Title Q1  Q2  Q3_1_og  \
1833  How author Michael Wolff got his &apos;fly-on-...  2  99     99.0   
358   Report: Trump uses crude term while attacking ...  1   2      6.0   
257   Israel gives African migrants 3 months to leav...  2  99     99.0   
835   The Latest: Trump says DACA bill has to overha...  1   2      6.0   
1048  Sanders: ‘I am not sure why' Trump is pushing ...  1   2      6.0   
...                                                 ... ..  ..      ...   
447    10 migrants dead, dozens missing off Libya coast  2  99     99.0   
1945  McConnell: 'Whoever gets to 60 wins'on immigra...  1   2      6.0   
295   Pelosi is optimistic about agreement on budget...  1   2      6.0   
986   South Korea Proposes Border Talks With North K...  2  99     99.0   
1390  Libel Law Review; Wall Part Of Deal; Joint New...  2  99     99.0   

      Q3_2_og Train Q3_1 Q3_2 Q3_3 Q3_4 Q3_5 Q3_6 Q3_7 Q3_8  
1833     99.0     1    0    0    0    0    0    0    0    0  
358       4.0     1    0    0    0    1    0    1    0    0  
257      99.0     1    0    0    0    0    0    0    0    0  
835       7.0     1    0    0    0    0    0    1    1    0  
1048      7.0     1    0    0    0    0    0    1    1    0  
...       ...   ...  ...  ...  ...  ...  ...  ...  ...  ...  
447      99.0     1    0    0    0    0    0    0    0    0  
1945     99.0     1    0    0    0    0    0    1    0    0  
295      99.0     1    0    0    0    0    0    1    0    0  
986      99.0     1    0    0    0    0    0    0    0    0  
1390     99.0     1    0    0    0    0    0    0    0    0  

[1000 rows x 19 columns]

**Understanding OpenAI's Charging Mechanism for Classification Tasks:

OpenAI charges based on the number of tokens processed. In the context of our classification task, this includes both the question tokens and the answer tokens. 

Here's a breakdown:

Question Tokens: These are the tokens present in the question you're asking the model. Given the nature of our task, the question is usually quite lengthy, resulting in a higher number of tokens.

Answer Tokens: These are the tokens in the model's response. For our classification task, the answers are typically short (e.g., '1' or '2'), so they contribute fewer tokens.

**Cost Implication:

Every classification attempt incurs a cost of 1 * number of question tokens *price per token + once_verify_num * number of answer tokens *price per token.

If a retry is needed, the cost of question tokens will be incurred again, making retries expensive.

**Optimization Strategy:

It's more cost-effective to run the classification with a larger once_verify_num initially. This increases the chances of getting a converged result directly.
Running with a smaller once_verify_num and then needing multiple retries can be more expensive. This is because each retry incurs the cost of the question tokens again, which are typically much larger than the answer tokens.


**Recommendation: 

To optimize costs, consider setting a sufficiently large once_verify_num to increase the likelihood of obtaining a converged result in the first attempt, thereby minimizing the need for retries.



### Q1: Is this news article related to immigration in the United States? 
Note: Irrelevant articles include immigration out of the US and immigration issues in countries other than the US. An article that covers a list of stories (e.g., the top 10 news stories of this month) is also considered not relevant.

1)	Yes

2)	No (End of coding; enter “99” for the rest of the cells)


In [5]:
# Enter the prompt
prompt_Q1 = """Here's a news article headline. Please code it based on the following criteria:
    Q1. **Relevance to U.S. Immigration**: Is the headline relevant to U.S. immigration? Note: Irrelevant articles include immigration out of the US and immigration issues in countries other than the US. An article that covers a list of stories (e.g., the top 10 news stories of this month) is also considered not relevant.
    - Return <1> for "Yes"
    - Return <2> for "No"
    Please only return "1" or "2" and do not provide any other information."""

In [6]:
# Q1 initial sample 
Q1_initial_sample = train_df.sample(SAMPLE_SIZE, random_state=SEED)
Q1_initial_sample.to_excel('03_Q1_initial_sample.xlsx', index=False)
Q1_initial_sample

# Setup permaters
if __name__ == "__main__":
    column_name = "Post_Title"  # the column name for the text to be classified
    model_name = "gpt-4"  # the GPT model to use
    label_num = 1  # the number of dimension/theme of this variable
    valid_values = ['1', '2']  # the valid answers from this question
    temperature = 0.7  # temperature 
    q_name = "Q1"  # the name of this question/variable
    once_verify_num = 3  # the numbers of results generated from GPT 
    max_verify_retry = 5  # the number of retries if the result is not converged
    prompt = prompt_Q1 # prompt

    # Initialize GPT Classifier
    gpt_classifier = GPTClassifier()

    # Setup classification task
    classification_task = ClassificationTask(
        column=column_name,
        prompt=prompt,
        model_name=model_name,
        label_num=label_num,
        valid_values=valid_values,
        temperature=temperature,
        q_name=q_name,
        once_verify_num=once_verify_num,
        max_verify_retry=max_verify_retry
    )

    # Classify and save the result
    result_df_q1_first_try = gpt_classifier.classify_df(Q1_initial_sample, classification_task)
    
    # Save to Excel
    result_df_q1_first_try.to_excel("04_Q1_initial_sample_result.xlsx")


2023-09-19 17:11:47.296 | INFO     | gpt_classify_function:classify_df:175 - Classifying 1/200 8 migrants dead, 84 rescued from sinking boat off Libya
2023-09-19 17:11:48.282 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:11:48.283 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:11:48.284 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:11:48.284 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for 8 migrants dead, 84 rescued from sinking boat off Libya
2023-09-19 17:11:48.287 | INFO     | gpt_classify_function:classify_df:175 - Classifying 2/200 : Apple iCloud Users in United States Swept up in Data Migration to Chinese Company
2023-09-19 17:11:48.997 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:11:48.998 | DEBUG    | gpt_classify_function:classify:139 - Va

2023-09-19 17:11:53.814 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:11:53.815 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Congress To Take Up DACA, Border Wall As It Advances On 2018 Agenda
2023-09-19 17:11:53.819 | INFO     | gpt_classify_function:classify_df:175 - Classifying 10/200 Senators on verge of bipartisan immigration deal
2023-09-19 17:11:54.418 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:11:54.419 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:11:54.419 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:11:54.419 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Senators on verge of bipartisan immigration deal
2023-09-19 17:11:54.422 | INFO     | gpt_classify_function:classify_df:175 - Class

2023-09-19 17:11:59.411 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:11:59.412 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:11:59.413 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:11:59.413 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Trump criticized immigration from 's---hole' countries: report | TheHill
2023-09-19 17:11:59.418 | INFO     | gpt_classify_function:classify_df:175 - Classifying 19/200 ICE to proceed with deportation of paraplegic boy's sole provider
2023-09-19 17:11:59.878 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:11:59.879 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:11:59.880 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3

2023-09-19 17:12:03.437 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for German conservatives call for tougher migrant age checks
2023-09-19 17:12:03.440 | INFO     | gpt_classify_function:classify_df:175 - Classifying 27/200 Lewandowski Adamant DACA Deal Will Include Border Wall
2023-09-19 17:12:03.845 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:12:03.846 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:12:03.847 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:12:03.847 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Lewandowski Adamant DACA Deal Will Include Border Wall
2023-09-19 17:12:03.850 | INFO     | gpt_classify_function:classify_df:175 - Classifying 28/200 Trump wants DACA with the border wall and immigration system changes - CNNPolitics
2023-09-19 17:12:04.2

2023-09-19 17:12:08.357 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:12:08.358 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:12:08.358 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:12:08.359 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Letter: Splitting Up Families: A Heartless Migrant Policy
2023-09-19 17:12:08.362 | INFO     | gpt_classify_function:classify_df:175 - Classifying 36/200 Trump administration's new immigration decision is shortsighted and cruel
2023-09-19 17:12:08.867 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:12:08.868 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:12:08.869 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023

...

2023-09-19 17:13:23.617 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for US Republicans unveil immigration bill, Trump demands wall funds
2023-09-19 17:13:23.621 | INFO     | gpt_classify_function:classify_df:175 - Classifying 165/200 Democrats, GOP Far Apart On Immigration Deal, Raising Government Shutdown Risk
2023-09-19 17:13:24.033 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:13:24.033 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:13:24.034 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:13:24.034 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Democrats, GOP Far Apart On Immigration Deal, Raising Government Shutdown Risk
2023-09-19 17:13:24.037 | INFO     | gpt_classify_function:classify_df:175 - Classifying 166/200 Republicans are blaming Trump adviser Stephen 

2023-09-19 17:13:29.274 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:13:29.274 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:13:29.275 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Australia’s Prime Minister Warns of ‘Gang Violence’ by African Migrants
2023-09-19 17:13:29.279 | INFO     | gpt_classify_function:classify_df:175 - Classifying 174/200 Trump administration to end special protections for Salvadoran immigrants
2023-09-19 17:13:29.762 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:13:29.763 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:13:29.764 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:13:29.764 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified

2023-09-19 17:13:34.990 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:13:34.990 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:13:34.991 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:13:34.991 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Confusion over Trump's border wall delays spending talks | TheHill
2023-09-19 17:13:34.994 | INFO     | gpt_classify_function:classify_df:175 - Classifying 183/200 The Memo: Immigration battle tests activists’ muscle | TheHill
2023-09-19 17:13:35.519 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:13:35.520 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:13:35.521 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-

2023-09-19 17:13:39.343 | INFO     | gpt_classify_function:classify_df:175 - Classifying 191/200 Cabinet official: Immigration plans may include citizenship
2023-09-19 17:13:39.345 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1'] Cabinet official: Immigration plans may include citizenship
2023-09-19 17:13:39.346 | INFO     | gpt_classify_function:classify_df:175 - Classifying 192/200 Border inspections of electronic devices hits record high
2023-09-19 17:13:40.234 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:13:40.234 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:13:40.235 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:13:40.235 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Border inspections of electronic devices hits record high
2023-09-19 17:13:40.239 | INFO     | gpt_

2023-09-19 17:13:45.023 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Trump aides and congressional leaders set to restart talks on budget and immigration - LA Times
2023-09-19 17:13:45.029 | INFO     | gpt_classify_function:classify_df:175 - Classifying 200/200 Motel 6 Gave Guest Info To Immigration Agents, Washington State AG Alleges
2023-09-19 17:13:45.631 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:13:45.632 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:13:45.633 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:13:45.633 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Motel 6 Gave Guest Info To Immigration Agents, Washington State AG Alleges


In [7]:
# check if any colomn has error or can not converge after the max_verify_retry that needs human validation
review_human_validation_rows(df=result_df_q1_first_try, text_column="Post_Title", 
                                        valid_values= ['1', '2'] ,  
                                        classification_columns=["Q1_1_classification"])


No row needs human validation, please proceed


ID  ID_original                                  GUID  \
0    1145         5414  49b3e083-e587-4375-ba6a-e8401a5b6d70   
1    1766         8173  21ed8bc7-3fde-427d-94a4-ad17f97b6d16   
2      27          118  5f22b40f-75cb-4a21-bd3f-b9f172f39e82   
3     209         1016  693eb477-d9e4-4ca6-990f-a2567d73494b   
4    1866         8581  2676ba34-6326-4191-b36c-5375ec362dde   
..    ...          ...                                   ...   
195  1927          163  0ba254e8-fc2b-4eef-9426-4a3cbd3ee70d   
196   335         1641  8fb8f1eb-7d19-4e8b-9816-e8c5f99363a8   
197  1744         8068  28d7ef5e-2cc1-463a-9444-f678a2c5fc0c   
198   144          693  d18efd8e-8b8c-4644-8321-396489e8160a   
199  1752         8108  a28523c0-363a-4931-8a0c-1549c452f75c   

             Date (GMT)                                                URL  \
0   2018-01-06 16:17:44  http://www.foxnews.com/world/2018/01/06/8-migr...   
1   2018-01-11 15:57:00  http://www.newsweek.com/apple-icloud-users-uni...   
2   2018-01-09 18:19:26  http://www.foxnews.com/entertainment/2018/01/0...   
3   2018-01-12 17:56:20  https://www.washingtonpost.com/politics/trumps...   
4   2018-01-12 00:44:46  https://www.usatoday.com/story/news/politics/2...   
..                  ...                                                ...   
195 2018-01-31 06:08:46  https://www.politico.com/story/2018/01/31/stat...   
196 2018-01-12 12:07:34  http://www.cnn.com/transcripts/1801/11/wolf.02...   
197 2018-01-09 20:39:36  https://www.nytimes.com/aponline/2018/01/09/us...   
198 2018-01-03 22:57:34  http://www.latimes.com/politics/washington/la-...   
199 2018-01-03 23:10:01  http://www.huffingtonpost.com/entry/motel-6-ic...   

                                            Post_Title Q1  Q2  Q3_1_og  \
0    8 migrants dead, 84 rescued from sinking boat ...  2  99     99.0   
1    : Apple iCloud Users in United States Swept up...  2  99     99.0   
2    CNN’s Chris Cuomo urges Americans to ‘get woke...  1   2      6.0   
3    Trump’s words reveal his misunderstanding of n...  1   2      6.0   
4    Report: Trump uses crude term while attacking ...  1   2      6.0   
..                                                 ... ..  ..      ...   
195  Democrats furious over Trump's immigration rhe...  1   2      6.0   
196  Will President Compromise on 2,000-Mile Concre...  2  99     99.0   
197  The Latest: Trump's Tone on Immigration Deal P...  1   2      6.0   
198  Trump aides and congressional leaders set to r...  1   2      6.0   
199  Motel 6 Gave Guest Info To Immigration Agents,...  1   1      2.0   

     Q3_2_og Train Q3_1 Q3_2 Q3_3 Q3_4 Q3_5 Q3_6 Q3_7 Q3_8 Q1_1_classification  
0       99.0     1    0    0    0    0    0    0    0    0                   2  
1       99.0     1    0    0    0    0    0    0    0    0                   2  
2        7.0     1    0    0    0    0    0    1    1    0                   1  
3        5.0     1    0    0    0    0    1    1    0    0                   1  
4        4.0     1    0    0    0    1    0    1    0    0                   1  
..       ...   ...  ...  ...  ...  ...  ...  ...  ...  ...                 ...  
195     99.0     1    0    0    0    0    0    1    0    0                   1  
196     99.0     1    0    0    0    0    0    0    0    0                   1  
197      7.0     1    0    0    0    0    0    1    1    0                   1  
198      7.0     1    0    0    0    0    0    1    1    0                   1  
199     99.0     1    0    1    0    0    0    0    0    0                   1  

[200 rows x 20 columns]

In [ ]:
# Caculate the accuraty
# method 1: maunally check row by row
# This methods is not presented due to timeness, 
# but the manual_validation function provides an interactive, user-friendly experience 
# for validating and correcting classifications, 
# making it accessible and effective for users without per-labeled data
# The user can simply click enter if they think the result is correct, 
# or enter the correct result if the reuslt is wrong

overall_accuracy, result_df =  manual_validation(result_df_q1_first_try, # the data frame
                      text_column="Post_Title",  # the column name for the text to be classified
                      num_dimensions=1, # the number of dimension/theme of this variable
                      column_names=["Q1_1_classification"], # the colomn name for the predicted results
                      valid_values= ['1', '2']) # the valid answers from this question

In [9]:
# method 2: auto check the accuracy if  already have the result in df
accuracy_Q1_first_try= compute_accuracy(df=result_df_q1_first_try, 
                                        predict_cols=["Q1_1_classification"], # the colomn name for predicted results
                                        actual_cols=["Q1"]) # the colomn name for acual results
accuracy_Q1_first_try

0.96

In [10]:
# The accuracy for Q1_first try is perrty high. Apply that to the whole testdf
if accuracy_Q1_first_try >= ACCEPTABLE_ACCURACY:
    # Process test df the funciton for Q1_first try 
    if __name__ == "__main__":
        column_name = "Post_Title" 
        model_name = "gpt-4" 
        label_num = 1 
        valid_values = ['1', '2']  
        temperature = 0.7 
        q_name = "Q1"  
        once_verify_num = 3   
        max_verify_retry = 5  
        prompt = prompt_Q1

        # Initialize GPT Classifier
        gpt_classifier = GPTClassifier()

        # Setup classification task
        classification_task = ClassificationTask(
            column=column_name,
            prompt=prompt,
            model_name=model_name,
            label_num=label_num,
            valid_values=valid_values,
            temperature=temperature,
            q_name=q_name,
            once_verify_num=once_verify_num,
            max_verify_retry=max_verify_retry
        )

        # Classify and save the result
        test_df = gpt_classifier.classify_df(test_df, classification_task)
        test_df.to_excel("05_Q1_testdf_result.xlsx")
    else:
        print("Needs more validation ")


2023-09-19 17:14:03.222 | INFO     | gpt_classify_function:classify_df:175 - Classifying 1/1001 Immigration officials target 7-Eleven shops amid Trump crackdown on undocumented migrants
2023-09-19 17:14:03.756 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:14:03.757 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:14:03.757 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:14:03.758 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Immigration officials target 7-Eleven shops amid Trump crackdown on undocumented migrants
2023-09-19 17:14:03.761 | INFO     | gpt_classify_function:classify_df:175 - Classifying 2/1001 Migrants Risk Death Crossing Alps to Reach France
2023-09-19 17:14:04.166 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:14:04.168 | DEBUG    | gpt

2023-09-19 17:14:07.845 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:14:07.846 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Trump defends vulgar immigrant comments, partly denies them
2023-09-19 17:14:07.848 | INFO     | gpt_classify_function:classify_df:175 - Classifying 10/1001 Fake Highway Signs Jab at New California Immigration Law
2023-09-19 17:14:08.304 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:14:08.305 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:14:08.306 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:14:08.306 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Fake Highway Signs Jab at New California Immigration Law
2023-09-19 17:14:08.309 | INFO     | gpt_classify_function:classify_df:17

2023-09-19 17:14:13.134 | INFO     | gpt_classify_function:classify_df:175 - Classifying 18/1001 DHS Checks 100 7-Eleven Stores for Immigration Fraud
2023-09-19 17:14:13.668 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:14:13.669 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:14:13.670 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:14:13.671 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for DHS Checks 100 7-Eleven Stores for Immigration Fraud
2023-09-19 17:14:13.675 | INFO     | gpt_classify_function:classify_df:175 - Classifying 19/1001 UN raises probable death toll in migrant boat sinking to 64
2023-09-19 17:14:14.374 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:14:14.375 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2']

2023-09-19 17:14:18.548 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:14:18.549 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:14:18.549 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Immigration Talks Proliferate on Capitol Hill, but No Deals
2023-09-19 17:14:18.553 | INFO     | gpt_classify_function:classify_df:175 - Classifying 27/1001 Fake Road Signs At California Border Mock The New Sanctuary State Status
2023-09-19 17:14:19.014 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:14:19.015 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:14:19.016 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:14:19.016 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Fak

2023-09-19 17:14:23.076 | INFO     | gpt_classify_function:classify_df:175 - Classifying 35/1001 Border inspections of electronic devices hits record high
2023-09-19 17:14:23.078 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1'] Border inspections of electronic devices hits record high
2023-09-19 17:14:23.078 | INFO     | gpt_classify_function:classify_df:175 - Classifying 36/1001 Trump blasts immigration ruling, calls U.S. court system 'broken and unfair'
2023-09-19 17:14:23.833 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:14:23.834 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:14:23.834 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:14:23.835 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Trump blasts immigration ruling, calls U.S. court system 'broken and unfair'
2023-09

...

2023-09-19 17:22:10.088 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:22:10.089 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Chuck Todd: Trump thinks 'white Europeans are good and brown immigrants are bad' | TheHill
2023-09-19 17:22:10.095 | INFO     | gpt_classify_function:classify_df:175 - Classifying 958/1001 Proposed law would require police to hold undocumented migrants if ICE requests it
2023-09-19 17:22:10.482 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:22:10.484 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:22:10.485 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:22:10.486 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Proposed law would require police to hold undocumented migrants if ICE r

2023-09-19 17:22:13.873 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:22:13.874 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:22:13.875 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for WATCH: Trump blames Democrats for impasse on immigration reform
2023-09-19 17:22:13.881 | INFO     | gpt_classify_function:classify_df:175 - Classifying 967/1001 Journalist killed in Mexican border state of Tamaulipas
2023-09-19 17:22:13.882 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['2'] Journalist killed in Mexican border state of Tamaulipas
2023-09-19 17:22:13.883 | INFO     | gpt_classify_function:classify_df:175 - Classifying 968/1001 Even if Congress says yes, Trump’s border wall faces these four big hurdles
2023-09-19 17:22:14.353 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:22:14.354

2023-09-19 17:22:17.643 | INFO     | gpt_classify_function:classify_df:175 - Classifying 976/1001 Feds raid 7-Eleven stores in immigration bust
2023-09-19 17:22:18.379 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:22:18.380 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:22:18.381 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:22:18.382 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Feds raid 7-Eleven stores in immigration bust
2023-09-19 17:22:18.387 | INFO     | gpt_classify_function:classify_df:175 - Classifying 977/1001 Trump Slams Immigrants from 'Shithole Countries'. Aired 7- 7:30a ET
2023-09-19 17:22:18.968 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:22:18.970 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['

2023-09-19 17:22:23.410 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:22:23.411 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:22:23.412 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:22:23.413 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for WATCH: Deadly California mudslides swallow lives, homes, cars
2023-09-19 17:22:23.418 | INFO     | gpt_classify_function:classify_df:175 - Classifying 986/1001 The immigration fight isn't really about the Dreamers — it's all politics | TheHill
2023-09-19 17:22:23.927 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:22:23.929 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:22:23.930 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications:

2023-09-19 17:22:28.081 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:22:28.082 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:22:28.083 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:22:28.084 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Report: Bannon-Breitbart ‘America First’ Agenda Battles ‘Economy First’ Globalists in Trump 2020 Strategy on Trade, Border Wall
2023-09-19 17:22:28.090 | INFO     | gpt_classify_function:classify_df:175 - Classifying 995/1001 Trump: Any Immigration Plan Without Border Wall 'Waste of Time'
2023-09-19 17:22:29.212 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:22:29.214 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:22:29.215 | INFO     | gpt_classify_function:mu

In [11]:
# check if any colomn has error or can not converge after the max_verify_retry that needs human validation
review_human_validation_rows(df=test_df, text_column="Post_Title", 
                                        valid_values= ['1', '2'] ,  
                                        classification_columns=["Q1_1_classification"])


No row needs human validation, please proceed


ID  ID_original                                  GUID  \
0      302         1504  8427d7da-077d-4557-b1f5-987abf8a10a5   
1     1405         6517  ab2e606d-9952-4f37-a362-e54e8ac8ea4e   
2      756         3710  2f2e22e4-20db-40e7-a877-ca574d1ba7b5   
3     1614         7442  c03828e7-e53c-47b7-9bdb-b4c33820854e   
4     1329         6144  790ad6df-bc2c-4199-9985-1258491e4f44   
...    ...          ...                                   ...   
996   1493         6882  b1412373-4338-4fdd-921a-dd1eb36285e1   
997    239         1147  453966ad-dbcf-43b6-82c3-44795077fa29   
998    514         2524  ebe0feb9-a8e9-4fd6-bd8d-3e57de1fe0fd   
999   1182         5567  a7803b28-642f-4624-aab8-ce81d14a0a4d   
1000  1906           17  64a7153b-cdcd-49fd-a3d5-d131c876ed28   

              Date (GMT)                                                URL  \
0    2018-01-11 23:48:07  https://www.yahoo.com/news/immigration-officia...   
1    2018-01-11 14:15:59  https://www.nytimes.com/reuters/2018/01/11/wor...   
2    2018-01-05 17:40:14  http://www.foxnews.com/us/2018/01/05/illegal-i...   
3    2018-01-07 21:25:50  https://www.yahoo.com/news/m/de1c6a57-6822-3e5...   
4    2018-01-09 12:24:44  http://www.cnn.com/transcripts/1801/08/ath.02....   
...                  ...                                                ...   
996  2018-01-08 21:57:16  http://www.motherjones.com/kevin-drum/2018/01/...   
997  2018-01-10 05:58:06  http://abcnews.go.com/International/wireStory/...   
998  2018-01-11 00:57:11  http://www.theblaze.com/news/2018/01/10/immigr...   
999  2018-01-10 09:07:51  https://www.yahoo.com/news/trump-suggests-comp...   
1000 2018-02-08 23:17:31  http://www.breitbart.com/big-government/2018/0...   

                                             Post_Title Q1  Q2  Q3_1_og  \
0     Immigration officials target 7-Eleven shops am...  1   2      1.0   
1     Migrants Risk Death Crossing Alps to Reach France  2  99     99.0   
2     Illegal immigrant who killed Kate Steinle like...  1   1      2.0   
3     Trump, seeking $18B for border wall, ties proj...  1   2      6.0   
4     Trump: Congress Must Fund Border Wall for DACA...  2  99     99.0   
...                                                 ... ..  ..      ...   
996   Donald Trump Wants to Waste a Lot of Money on ...  1   2      6.0   
997   The Latest: Feds object to judge's immigration...  1   2     99.0   
998   Immigration agents hit this popular business h...  1   2      1.0   
999   Trump Suggests Comprehensive Immigration Refor...  1   2      6.0   
1000  Establishment Media Rally for Chain Migration ...  1   2      6.0   

      Q3_2_og Train Q3_1 Q3_2 Q3_3 Q3_4 Q3_5 Q3_6 Q3_7 Q3_8  \
0         2.0     1    1    1    0    0    0    0    0    0   
1        99.0     1    0    0    0    0    0    0    0    0   
2        99.0     1    0    1    0    0    0    0    0    0   
3         1.0     1    1    0    0    0    0    1    0    0   
4        99.0     1    0    0    0    0    0    0    0    0   
...       ...   ...  ...  ...  ...  ...  ...  ...  ...  ...   
996       1.0     1    1    0    0    0    0    1    0    0   
997      99.0     1    0    0    0    0    0    0    0    0   
998      99.0     1    1    0    0    0    0    0    0    0   
999      99.0     1    0    0    0    0    0    1    0    0   
1000     99.0     1    0    0    0    0    0    1    0    0   

     Q1_1_classification  
0                      1  
1                      2  
2                      1  
3                      1  
4                      1  
...                  ...  
996                    1  
997                    1  
998                    1  
999                    1  
1000                   1  

[1001 rows x 20 columns]

In [12]:
# Caculate the total accuracy for Q1 on the test df
accuracy_Q1_test_df= compute_accuracy(df=test_df, 
                                        predict_cols=["Q1_1_classification"], 
                                        actual_cols=["Q1"])
print("Q1 accuracy on test df: ",accuracy_Q1_test_df)

Q1 accuracy on test df:  0.954045954045954


### Q2: What is the focus of the news story? 
1)	The story focuses on one incident or event related to immigration.

2)	The story focuses on the issue of immigration as an ongoing problem, discusses its causes and solutions, etc.

Note. If Q1 ==2 (not news article about immgreation), we don't need to code this question. It will automatically be 99. 

In [13]:
prompt_Q2 = """Here's a news article headline. Please code it based on the following criteria:
                Q2: What is the focus of the news story? 
                1)The story focuses on one incident or event related to immigration: The story focuses on a single case such as information about one individual’s story about crossing the border. Often times, stories coded in episodic frame only contain the facts of one incident. 
                Example: "Illegal Immigrant in San Francisco Killing Sentenced to Time Served on Weapons Charge"; "ICE Raids Target Illinois 7-Eleven Stores, 21 Arrested Nationwide"; "Trump Administration Tells 200,000 Salvadorans To Leave Or Get Deported: Reports";"Smuggler Packs 19 Migrants in Pickup Truck near Texas Border"
                Return "1" for "The story focuses on one incident or event related to immigration."

                2)The story focuses on the issue of immigration as an ongoing problem, discusses its causes and solutions, etc.: The story focuses on the issue of immigration in general such as suggesting causes of or solutions to the problem. Generally speaking, news stories about protests should be considered thematic because protests are usually about advocating for a certain solution to the immigration issue. Stories that are about consequences of one immigrant's actions (e.g., the impact of one immigrant's crime on a community) are also considered thematic. 
                Example: "A Counterproductive Approach to a Broken Immigration System"; "CHAVEZ: Congress Could Fix Immigration — If Trump Plays Ball"; "Fact check: How much does illegal immigration cost America? Not nearly as much as Trump 
                Return "2" for "The story focuses on the issue of immigration as an ongoing problem, discusses its causes and solutions, etc.."

                Please only return "1" or "2" """


In [14]:
# Q2 initial sample 
# For Q2, I will sample from the train df which Q1 does not equal to 2, as if Q1 ==2, Q2 will automatically == 99
train_df_yes_immigration = train_df[train_df['Q1'] == "1"]
Q2_initial_sample = train_df_yes_immigration.sample(SAMPLE_SIZE, random_state=SEED)
Q2_initial_sample.to_excel('06_Q2_initial_sample.xlsx', index=False)


if __name__ == "__main__":
    # Setup parameters
    column_name = "Post_Title"  # the column name for the text to be classified
    model_name = "gpt-4"  # the GPT model to use
    label_num = 1  # the number of dimensions of this variable
    valid_values = ['1', '2']  # the valid answers from this question
    temperature = 0.7  # temperature 
    q_name = "Q2"  # the name of this question/variable
    once_verify_num = 3  # the numbers of results generated from GPT 
    max_verify_retry = 5  # the number of retries if the previous is not converged
    prompt = prompt_Q2

    # Initialize GPT Classifier
    gpt_classifier = GPTClassifier()

    # Setup classification task
    classification_task = ClassificationTask(
        column=column_name,
        prompt=prompt,
        model_name=model_name,
        label_num=label_num,
        valid_values=valid_values,
        temperature=temperature,
        q_name=q_name,
        once_verify_num=once_verify_num,
        max_verify_retry=max_verify_retry
    )

    # Classify and save the result
    result_df_q2_first_try = gpt_classifier.classify_df(Q2_initial_sample, classification_task)
    result_df_q2_first_try.to_excel("07_Q2_initial_sample_result.xlsx")


2023-09-19 17:22:49.878 | INFO     | gpt_classify_function:classify_df:175 - Classifying 1/200 Immigration Agents Raid Nearly 100 7-Eleven Stores Nationwide In Show Of Force
2023-09-19 17:22:50.656 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:22:50.657 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:22:50.658 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:22:50.658 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Immigration Agents Raid Nearly 100 7-Eleven Stores Nationwide In Show Of Force
2023-09-19 17:22:50.662 | INFO     | gpt_classify_function:classify_df:175 - Classifying 2/200 DC forecast: Gathering winter storm over wall vs. DACA, possible shutdown
2023-09-19 17:22:51.654 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:22:51.655 | DEBUG    | gpt

2023-09-19 17:22:56.701 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:22:56.701 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Illegal Immigrant in San Francisco Killing Sentenced to Time Served on Weapons Charge
2023-09-19 17:22:56.704 | INFO     | gpt_classify_function:classify_df:175 - Classifying 10/200 Trump: Wall 'Must'Be Part of Any DACA Deal
2023-09-19 17:22:57.674 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:22:57.676 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:22:57.677 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:22:57.678 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Trump: Wall 'Must'Be Part of Any DACA Deal
2023-09-19 17:22:57.683 | INFO     | gpt_classify_function:classify_df:175 -

2023-09-19 17:23:02.316 | INFO     | gpt_classify_function:classify_df:175 - Classifying 18/200 The Latest: Trump's Tone on Immigration Deal Pleases Schumer
2023-09-19 17:23:02.895 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:23:02.896 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:23:02.896 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:23:02.897 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for The Latest: Trump's Tone on Immigration Deal Pleases Schumer
2023-09-19 17:23:02.900 | INFO     | gpt_classify_function:classify_df:175 - Classifying 19/200 The Latest: White House Blasts Ruling on Immigrants Program
2023-09-19 17:23:03.444 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:23:03.445 | DEBUG    | gpt_classify_function:classify:139 - Valid results:

2023-09-19 17:23:09.268 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:23:09.269 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:23:09.270 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:23:09.271 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Trump thanks lawmakers for 'productive'immigration meeting, says deal must include border wall
2023-09-19 17:23:09.276 | INFO     | gpt_classify_function:classify_df:175 - Classifying 28/200 Trump wants to cut proven border security measures to fund his border wall fantasy
2023-09-19 17:23:09.878 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:23:09.879 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:23:09.879 | INFO     | gpt_classify_function:multi_verify:159 -

2023-09-19 17:23:14.677 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Trump faces more criticism from Congress over remarks on immigration | Jamie Dupree jamiedupree.blog.ajc.com
2023-09-19 17:23:14.682 | INFO     | gpt_classify_function:classify_df:175 - Classifying 36/200 Divided Democrats Face Liberal Backlash on Immigration
2023-09-19 17:23:15.277 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:23:15.277 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:23:15.278 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:23:15.278 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Divided Democrats Face Liberal Backlash on Immigration
2023-09-19 17:23:15.281 | INFO     | gpt_classify_function:classify_df:175 - Classifying 37/200 How ‘chain migration’ became a target in Trump’s imm

...

2023-09-19 17:24:37.188 | INFO     | gpt_classify_function:classify_df:175 - Classifying 159/200 Dale Wilcox on Trump Amnesty: Chain Migration ‘Not Ended Immediately’; Visa Lottery Numbers ‘Shifted’ to Other Categories
2023-09-19 17:24:37.896 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:24:37.896 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:24:37.897 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:24:37.897 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Dale Wilcox on Trump Amnesty: Chain Migration ‘Not Ended Immediately’; Visa Lottery Numbers ‘Shifted’ to Other Categories
2023-09-19 17:24:37.901 | INFO     | gpt_classify_function:classify_df:175 - Classifying 160/200 FACT CHECK: WaPo Claims 'Gang Of Eight' Immigration Bill Would Have Decreased Legal Immigration
2023-09-19 17:24:38.642 | DEBUG

2023-09-19 17:24:43.166 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:24:43.166 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:24:43.167 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Rand Paul Says Calling Trump 'A Racist'Hurts Immigration Talks
2023-09-19 17:24:43.170 | INFO     | gpt_classify_function:classify_df:175 - Classifying 168/200 White House ‘Hope’ for DACA Deal Includes Wall, Enforcement, Ending Lottery, and Chain Migration - Breitbart
2023-09-19 17:24:43.904 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:24:43.905 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:24:43.906 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:24:43.906 | SUCCESS  | gpt_classify_function:multi_v

2023-09-19 17:24:48.679 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Mark Krikorian: Trump Sounded 'More Like Jeb Bush'at Immigration Meeting
2023-09-19 17:24:48.683 | INFO     | gpt_classify_function:classify_df:175 - Classifying 176/200 Building the wall would be so worth it
2023-09-19 17:24:49.242 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:24:49.242 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:24:49.243 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:24:49.243 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Building the wall would be so worth it
2023-09-19 17:24:49.247 | INFO     | gpt_classify_function:classify_df:175 - Classifying 177/200 Trump comments highlight racial impact of migration platform
2023-09-19 17:24:50.214 | DEBUG    | gpt_classify_functio

2023-09-19 17:24:54.367 | INFO     | gpt_classify_function:classify_df:175 - Classifying 185/200 Homeland chief: Wait and see on citizenship for immigrants
2023-09-19 17:24:56.501 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:24:56.501 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:24:56.502 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:24:56.502 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Homeland chief: Wait and see on citizenship for immigrants
2023-09-19 17:24:56.506 | INFO     | gpt_classify_function:classify_df:175 - Classifying 186/200 House Dem Caucus Chair Crowley: We Want a Clean DACA Bill, A Border Wall Is a ‘Waste’ of Money
2023-09-19 17:24:57.103 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:24:57.105 | DEBUG    | gpt_classify_funct

2023-09-19 17:25:01.552 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:25:01.552 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:25:01.553 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Trump, GOP Congratulate Selves For Immigration Meeting 4 Months Into DACA Crisis
2023-09-19 17:25:01.557 | INFO     | gpt_classify_function:classify_df:175 - Classifying 195/200 This Trump appointee wants to charge elected officials with crimes over their policy stances on immigration.
2023-09-19 17:25:02.246 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:25:02.247 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:25:02.248 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:25:02.248 | SUCCESS  | gpt_classif

In [15]:
# check if any colomn has error or can not converge after the max_verify_retry that needs human validation
review_human_validation_rows(df=result_df_q2_first_try, text_column="Post_Title", 
                                        valid_values= ['1', '2'] ,  
                                        classification_columns=["Q2_1_classification"])


No row needs human validation, please proceed


ID  ID_original                                  GUID  \
0      60          272  f924a7e0-3247-4f95-8c88-44947bf098ca   
1     943         4525  ae304fbc-2257-4064-becc-b00ee6c7d23d   
2    1184         5575  586c8fbc-a89a-4059-ac23-0e096034c4fe   
3    1911           27  ef3e3c6e-88a9-43f9-8db1-0056317e83e2   
4     896         4343  dc557291-63e5-45ac-92f7-58d3f5ce4c67   
..    ...          ...                                   ...   
195  1345         6222  68ca08eb-cb23-4902-b9dc-d176c2c6c9ef   
196  1644         7613  dea316a7-d96b-4287-9ac8-fda941ba47be   
197  1584         7303  3d7ea54c-d9de-4394-9b6f-f1fb9049a854   
198  1751         8106  818d9a80-dcf6-4fac-b7c0-88b52a67f0c5   
199   683         3368  621b2b80-1b43-4dd3-aebb-e158ee049bc7   

             Date (GMT)                                                URL  \
0   2018-01-11 03:19:53  https://www.huffingtonpost.com/entry/immigrati...   
1   2018-01-07 19:08:41  http://www.foxnews.com/politics/2018/01/07/dc-...   
2   2018-01-12 12:31:58  https://www.nytimes.com/aponline/2018/01/12/us...   
3   2018-01-26 04:15:14  http://thehill.com/homenews/senate/370810-warr...   
4   2018-01-03 22:24:16  https://www.usatoday.com/story/news/nation-now...   
..                  ...                                                ...   
195 2018-01-07 15:03:51  https://www.nytimes.com/2018/01/07/nyregion/im...   
196 2018-01-11 11:10:33  http://thehill.com/homenews/administration/368...   
197 2018-01-02 14:37:25  http://dailycaller.com/2018/01/02/border-patro...   
198 2018-01-05 16:15:25  http://www.foxnews.com/us/2018/01/05/illegal-i...   
199 2018-01-12 09:14:17  http://dailycaller.com/2018/01/11/heres-trumps...   

                                            Post_Title Q1 Q2  Q3_1_og  \
0    Immigration Agents Raid Nearly 100 7-Eleven St...  1  1     99.0   
1    DC forecast: Gathering winter storm over wall ...  1  2      7.0   
2    The Latest: Trump Defends Immigration Stance i...  1  2      6.0   
3    Warren rips Trump immigration proposal: It's'i...  1  2      6.0   
4    Immigration officials 'deeply disturbed'by cou...  1  2      7.0   
..                                                 ... .. ..      ...   
195  Judge Faults U.S. for Holding Immigrant Defend...  1  2      4.0   
196  The Memo: Immigration battle tests activists’ ...  1  2      8.0   
197  Border Patrol President: Because Of Trump ‘201...  1  2      6.0   
198  Illegal immigrant who killed Kate Steinle like...  1  1      1.0   
199  Here's Trump's Plan For Getting Mexico To Pay ...  1  2      6.0   

     Q3_2_og Train Q3_1 Q3_2 Q3_3 Q3_4 Q3_5 Q3_6 Q3_7 Q3_8 Q2_1_classification  
0       99.0     1    0    0    0    0    0    0    0    0                   1  
1       99.0     1    0    0    0    0    0    0    1    0                   2  
2       99.0     1    0    0    0    0    0    1    0    0                   2  
3        7.0     1    0    0    0    0    0    1    1    0                   2  
4       99.0     1    0    0    0    0    0    0    1    0                   1  
..       ...   ...  ...  ...  ...  ...  ...  ...  ...  ...                 ...  
195     99.0     1    0    0    0    1    0    0    0    0                   1  
196     99.0     1    0    0    0    0    0    0    0    1                   2  
197     99.0     1    0    0    0    0    0    1    0    0                   2  
198     99.0     1    1    0    0    0    0    0    0    0                   1  
199      1.0     1    1    0    0    0    0    1    0    0                   2  

[200 rows x 20 columns]

In [ ]:
# caculate the accuraty
# method 1: maunally check row by row
overall_accuracy, result_df =  manual_validation(result_df_q2_first_try, 
                      text_column="Post_Title", 
                      num_dimensions=1, 
                      column_names=["Q2_1_classification"], 
                      valid_values= ['1', '2'])

In [16]:
# method 2: auto check the accuracy if we already have the result in df
accuracy_df_q2_first_try= compute_accuracy(df=result_df_q2_first_try, 
                                        predict_cols=["Q2_1_classification"], 
                                        actual_cols=["Q2"])
accuracy_df_q2_first_try

0.905

In [18]:
# The accuracy is good, work on the Q2 for the test df
# One more logic for Q2, if Q1 == 2, we will skip it and directly enter 99
# Filter out rows where Q1 is "2" and classify the remaining rows
filtered_df = test_df[test_df['Q1'] == "1"]
filtered_df.to_excel('08_Q2_testdf_Q1_yes.xlsx', index=False)

if accuracy_df_q2_first_try >= ACCEPTABLE_ACCURACY:
    # Process test df the function for Q2_first try where Q1_1 classfication ==1
    if __name__ == "__main__":
        # Setup parameters
        column_name = "Post_Title"  # the column name for the text to be classified
        model_name = "gpt-4"  # the GPT model to use
        label_num = 1  # the number of dimensions of this variable
        valid_values = ['1', '2']  # the valid answers from this question
        temperature = 0.7  # temperature 
        q_name = "Q2"  # the name of this question/variable
        once_verify_num = 3  # the numbers of results generated from GPT 
        max_verify_retry = 5  # the number of retries if the previous is not converged
        prompt = prompt_Q2

        # Initialize GPT Classifier
        gpt_classifier = GPTClassifier()

        # Setup classification task
        classification_task = ClassificationTask(
            column=column_name,
            prompt=prompt,
            model_name=model_name,
            label_num=label_num,
            valid_values=valid_values,
            temperature=temperature,
            q_name=q_name,
            once_verify_num=once_verify_num,
            max_verify_retry=max_verify_retry
        )
        
        classified_df = gpt_classifier.classify_df(filtered_df, classification_task)
        classified_df.to_excel("09_Q2_testdf_Q1_yes_result.xlsx")
    else:
        print("Needs more validation ")


2023-09-19 17:25:29.653 | INFO     | gpt_classify_function:classify_df:175 - Classifying 1/800 Immigration officials target 7-Eleven shops amid Trump crackdown on undocumented migrants
2023-09-19 17:25:30.304 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:25:30.305 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:25:30.306 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:25:30.306 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Immigration officials target 7-Eleven shops amid Trump crackdown on undocumented migrants
2023-09-19 17:25:30.309 | INFO     | gpt_classify_function:classify_df:175 - Classifying 2/800 Illegal immigrant who killed Kate Steinle likely will be sentenced to time served
2023-09-19 17:25:30.311 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1'] Illegal immigrant w

2023-09-19 17:25:35.346 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Taking away their children won't stop Central American border crossers
2023-09-19 17:25:35.349 | INFO     | gpt_classify_function:classify_df:175 - Classifying 10/800 NumbersUSA Backs House DACA Amnesty Bill: 'No Way' Congress Will Give Us E-Verify, End Chain Migration ‘Without Trade-Offs'
2023-09-19 17:25:35.974 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:25:35.976 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:25:35.977 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:25:35.977 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for NumbersUSA Backs House DACA Amnesty Bill: 'No Way' Congress Will Give Us E-Verify, End Chain Migration ‘Without Trade-Offs'
2023-09-19 17:25:35.984 | INFO     | gpt_classif

2023-09-19 17:25:41.203 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:25:41.204 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:25:41.205 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:25:41.205 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Immigrant acquitted of killing is sentenced for gun charge
2023-09-19 17:25:41.209 | INFO     | gpt_classify_function:classify_df:175 - Classifying 19/800 NY state offers help to Salvadorans facing deportation
2023-09-19 17:25:41.779 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:25:41.780 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:25:41.780 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:25:41.78

2023-09-19 17:25:46.403 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:25:46.403 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Trump Says He Is Open to Sweeping Deal on Immigration
2023-09-19 17:25:46.407 | INFO     | gpt_classify_function:classify_df:175 - Classifying 27/800 Chuck Todd: Trump’s ‘Core Beliefs’ Are ‘White Europeans Are Good and Brown Immigrants Are Bad’
2023-09-19 17:25:46.950 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:25:46.952 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:25:46.953 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:25:46.954 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Chuck Todd: Trump’s ‘Core Beliefs’ Are ‘White Europeans Are Good and Brown Immigrants Are Bad’
2023

2023-09-19 17:25:51.331 | INFO     | gpt_classify_function:classify_df:175 - Classifying 35/800 Trump Administration Seeks $18 Billion Over Decade to Expand Border Wall - WSJ
2023-09-19 17:25:51.963 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:25:51.964 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:25:51.964 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:25:51.965 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Trump Administration Seeks $18 Billion Over Decade to Expand Border Wall - WSJ
2023-09-19 17:25:51.968 | INFO     | gpt_classify_function:classify_df:175 - Classifying 36/800 DACA recipient in ICE custody after taking a wrong turn at the border
2023-09-19 17:25:52.750 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:25:52.752 | DEBUG    | gpt_c

...

2023-09-19 17:33:25.565 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:33:25.566 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:33:25.567 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:33:25.568 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Chuck Todd: Trump thinks 'white Europeans are good and brown immigrants are bad' | TheHill
2023-09-19 17:33:25.574 | INFO     | gpt_classify_function:classify_df:175 - Classifying 766/800 Proposed law would require police to hold undocumented migrants if ICE requests it
2023-09-19 17:33:26.172 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:33:26.173 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:33:26.174 | INFO     | gpt_classify_function:multi_verify:159 - Tr

2023-09-19 17:33:30.654 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:33:30.655 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Even if Congress says yes, Trump’s border wall faces these four big hurdles
2023-09-19 17:33:30.660 | INFO     | gpt_classify_function:classify_df:175 - Classifying 774/800 The Number Of Electronic Devices Searched At The Border Surged In 2017
2023-09-19 17:33:31.399 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '2']
2023-09-19 17:33:31.400 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['2']]
2023-09-19 17:33:31.401 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 2), ('2', 1)]
2023-09-19 17:33:31.402 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for The Number Of Electronic Devices Searched At The Border Surged In 2017
2023-09-19 17:33:31

Rate limit reached for default-gpt-4 in organization org-oC4UJKgkigzBaVPzhCPROXBW on tokens per min. Limit: 40000 / min. Please try again in 1ms. Contact us through our help center at help.openai.com if you continue to have issues.
Request timed out. Retrying...


2023-09-19 17:33:38.445 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['1', '1', '1']
2023-09-19 17:33:38.446 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1'], ['1'], ['1']]
2023-09-19 17:33:38.447 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1', 3)]
2023-09-19 17:33:38.448 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1 for Antonio Sabato Jr.: I'm an Immigrant Who Supports the Wall
2023-09-19 17:33:38.454 | INFO     | gpt_classify_function:classify_df:175 - Classifying 783/800 Nicolle Wallace: Trump 'speaks in a racist way about Haitians'
2023-09-19 17:33:40.288 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:33:40.289 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:33:40.290 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17

2023-09-19 17:33:44.001 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Trump Is Right: Giving Priority To 'The Wall' Is For The Good Of All
2023-09-19 17:33:44.006 | INFO     | gpt_classify_function:classify_df:175 - Classifying 792/800 Flashback: Trump Campaign Ad Mocked Jeb Bush's 'Act of Love' Comment on Illegal Immigration - Breitbart
2023-09-19 17:33:44.814 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['2', '2', '2']
2023-09-19 17:33:44.815 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['2'], ['2'], ['2']]
2023-09-19 17:33:44.817 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('2', 3)]
2023-09-19 17:33:44.817 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 2 for Flashback: Trump Campaign Ad Mocked Jeb Bush's 'Act of Love' Comment on Illegal Immigration - Breitbart
2023-09-19 17:33:44.823 | INFO     | gpt_classify_function:classify_df:175 - Classifying 

In [19]:
# check if any colomn has error or can not converge after the max_verify_retry that needs human validation
review_human_validation_rows(df=classified_df, text_column="Post_Title", 
                                        valid_values= ['1', '2'] ,  
                                        classification_columns=["Q2_1_classification"])


No row needs human validation, please proceed


ID  ID_original                                  GUID  \
0     302         1504  8427d7da-077d-4557-b1f5-987abf8a10a5   
1     756         3710  2f2e22e4-20db-40e7-a877-ca574d1ba7b5   
2    1614         7442  c03828e7-e53c-47b7-9bdb-b4c33820854e   
3    1329         6144  790ad6df-bc2c-4199-9985-1258491e4f44   
4    1477         6830  59747e7c-fba0-4d85-9d51-094168531e32   
..    ...          ...                                   ...   
795  1493         6882  b1412373-4338-4fdd-921a-dd1eb36285e1   
796   239         1147  453966ad-dbcf-43b6-82c3-44795077fa29   
797   514         2524  ebe0feb9-a8e9-4fd6-bd8d-3e57de1fe0fd   
798  1182         5567  a7803b28-642f-4624-aab8-ce81d14a0a4d   
799  1906           17  64a7153b-cdcd-49fd-a3d5-d131c876ed28   

             Date (GMT)                                                URL  \
0   2018-01-11 23:48:07  https://www.yahoo.com/news/immigration-officia...   
1   2018-01-05 17:40:14  http://www.foxnews.com/us/2018/01/05/illegal-i...   
2   2018-01-07 21:25:50  https://www.yahoo.com/news/m/de1c6a57-6822-3e5...   
3   2018-01-09 12:24:44  http://www.cnn.com/transcripts/1801/08/ath.02....   
4   2018-01-14 22:47:56  https://www.dailykos.com/stories/2018/1/14/173...   
..                  ...                                                ...   
795 2018-01-08 21:57:16  http://www.motherjones.com/kevin-drum/2018/01/...   
796 2018-01-10 05:58:06  http://abcnews.go.com/International/wireStory/...   
797 2018-01-11 00:57:11  http://www.theblaze.com/news/2018/01/10/immigr...   
798 2018-01-10 09:07:51  https://www.yahoo.com/news/trump-suggests-comp...   
799 2018-02-08 23:17:31  http://www.breitbart.com/big-government/2018/0...   

                                            Post_Title Q1  Q2  Q3_1_og  \
0    Immigration officials target 7-Eleven shops am...  1   2      1.0   
1    Illegal immigrant who killed Kate Steinle like...  1   1      2.0   
2    Trump, seeking $18B for border wall, ties proj...  1   2      6.0   
3    Trump: Congress Must Fund Border Wall for DACA...  2  99     99.0   
4    Donald Trump this past Tuesday held a bipartis...  1   2      6.0   
..                                                 ... ..  ..      ...   
795  Donald Trump Wants to Waste a Lot of Money on ...  1   2      6.0   
796  The Latest: Feds object to judge's immigration...  1   2     99.0   
797  Immigration agents hit this popular business h...  1   2      1.0   
798  Trump Suggests Comprehensive Immigration Refor...  1   2      6.0   
799  Establishment Media Rally for Chain Migration ...  1   2      6.0   

     Q3_2_og  ... Q3_2 Q3_3 Q3_4 Q3_5 Q3_6 Q3_7 Q3_8 Q1_1_classification  \
0        2.0  ...    1    0    0    0    0    0    0                   1   
1       99.0  ...    1    0    0    0    0    0    0                   1   
2        1.0  ...    0    0    0    0    1    0    0                   1   
3       99.0  ...    0    0    0    0    0    0    0                   1   
4        7.0  ...    0    0    0    0    1    1    0                   1   
..       ...  ...  ...  ...  ...  ...  ...  ...  ...                 ...   
795      1.0  ...    0    0    0    0    1    0    0                   1   
796     99.0  ...    0    0    0    0    0    0    0                   1   
797     99.0  ...    0    0    0    0    0    0    0                   1   
798     99.0  ...    0    0    0    0    1    0    0                   1   
799     99.0  ...    0    0    0    0    1    0    0                   1   

    accurate Q2_1_classification  
0       True                   1  
1       True                   1  
2       True                   2  
3      False                   1  
4       True                   2  
..       ...                 ...  
795     True                   2  
796     True                   1  
797     True                   1  
798     True                   2  
799     True                   2  

[800 rows x 22 columns]

In [20]:
# Merge the result to test_df and enter "99" for the rows that Q1_1_classification= "2"

# Step 1: Create a new column named Q2_1_classification in test_df
test_df['Q2_1_classification'] = None

# Step 2: Copy values from classified_df to test_df where other columns are the same
for idx, row in test_df.iterrows():
    mask = (classified_df.drop(columns=['Q2_1_classification']) == row.drop(labels=['Q2_1_classification'])).all(axis=1)
    if mask.any():
        test_df.at[idx, 'Q2_1_classification'] = classified_df.loc[mask, 'Q2_1_classification'].iloc[0]

# Step 3: Set Q2_1_classification to "99" where Q1_1_classification is "2"
test_df.loc[test_df['Q1_1_classification'] != "1", 'Q2_1_classification'] = "99"
test_df.to_excel("10_Q2_testdf_result_whole.xlsx")


In [22]:
# caculate the accuraty for Q1 = 1
accuracy_df_q2_classified_df= compute_accuracy(df=classified_df, 
                                        predict_cols=["Q2_1_classification"], 
                                        actual_cols=["Q2"])
accuracy_df_q2_classified_df

0.86375

In [23]:
# caculate the accuraty for all
accuracy_df_q2_test_df= compute_accuracy(df=test_df, 
                                        predict_cols=["Q2_1_classification"], 
                                        actual_cols=["Q2"])
print("Q2 accuracy on test df: ",accuracy_df_q2_test_df)

Q2 accuracy on test df:  0.8771228771228772


### Q3-1/2: What is the main theme of this news story?  
Note: Code up to two dominant themes. Consider the following headline as an example: “A caravan of grandparents are crossing the country to protest family separation in Texas.” This headline should be coded as both 8) Public opinion and 3) Family. Whichever theme that comes first in the headline should be entered as Theme1. Enter “99” if there is no theme identified for both Q3-1 and Q3-2. 

1	Economic consequences

2	Crime/safety

3	Family

4	Immigrant wellbeing

5	Culture/society

6	Politics

7	Legislation/regulation

8	Public opinion

99  None of the above 

For better performance, we convert Q3 to code if each of the topics exists within the headline.

#### This is an example of *multi-theme classfication*.



In [24]:
prompt_Q3 = '''Here's a news article headline. Please label if it belongs to the following theme. 
            Return <1> if this headline belongs to these themes and return <0> if it does not belong to the themes.
            Please identify up to two dominant themes from the headline, which means you can have a max of 2 <1> in the answer you generated.
            You don't have to label two topic if you don't fint it apply. Just enter 0s.
            - Economic consequences: The story is about economic benefits or costs, or the costs involving immigration-related issues, including: Cost of mass deportation; Economic benefits of immigration (more tax revenue, cheap labor; Economic costs of immigration (taking jobs from Americans, immigrants using healthcare and educational services, overcrowding, housing concerns)
            - Crime/safety: The story is about threats to American's safety, including: Immigration described as a major cause of increased rates of crime, gangs, drug trafficking, etc; Immigrants described as law-breakers who deserve punishment; Immigration described as a threat to national security via terrorism
            - Family: The story is about the impact of immigration on families, including: Separating children from parents; Breaking up multi-generational families; Interfering with children's continued schooling
            - Immigrant wellbeing: This story is about the negative impact of the immigration process on immigrants, including: Prejudice and bias toward immigrants; Physical and/or mental health or safety of immigrants; Immigration policies described as violations of immigrants' civil rights and liberties; Immigration policies regarding illegal immigrants described as unfair to immigrants who have waited to become citizens the legal way
            - Culture/society: This story is about societal-wide factors or consequences related to immigration, including:; Immigration as a threat to American cultural identity, way of living, the predominance of English and Christianity, etc.; Immigrants as isolated from the rest of America, unable to assimilate into communities; Immigration as part of the celebrated history of immigration in America / America-as-melting-pot; Immigration policies as exemplars of society's immorality; Impact of immigration on a specific subculture/community in the US
            - Politics:The story is mainly about the political issues around immigration, including: Political campaigns and upcoming elections (e.g., using immigration as a wedge issue or motivating force to get people to the polls); Fighting between the Democratic and Republican parties, or politicians; One political party or one politician’s stance on immigration. Therefore, when the news headline mentions a politician’s name, it often indicates the theme of politics
            - Legislation/regulation: The story is about issues related to regulating immigration through legislation and other institutional measures: New immigration legislation being introduced/argued over; Flaws in current/old legislation; Enforcement of current legislation
            - Public opinion: The study is about the public’s, including a specific community’s, reactions to immigration-related issues, including: Public opinion polls; Protests; Social media backlash; Community outrage; Celebrity responses/protests
            Answer using the JSON formet, [<0>,<0>,<0>,<0>,<0>,<0>,<0>,<0>]. Do not provide any other information'''


In [25]:
# Q3 initial sample 
# For Q3, I will still sample from the train df which Q1 does not equal to 2
train_df_yes_immigration = train_df[train_df['Q1_1_classification'] == "1"]
Q3_initial_sample = train_df_yes_immigration.sample(SAMPLE_SIZE, random_state=SEED)
Q3_initial_sample.to_excel("11_Q3_inital_sample.xlsx")
if __name__ == "__main__":
    # Setup parameters
    column_name = "Post_Title"  # the column name for the text to be classified
    model_name = "gpt-4"  # the GPT model to use
    label_num = 8  # the number of dimensions of this variable
    valid_values = ['0', '1']  # the valid answers from this question
    temperature = 0.7  # temperature 
    q_name = "Q3"  # the name of this question/variable
    once_verify_num = 3  # the numbers of results generated from GPT 
    max_verify_retry = 5  # the number of retries if the previous is not converged
    prompt = prompt_Q3

    # Initialize GPT Classifier
gpt_classifier = GPTClassifier()

    # Setup classification task
classification_task = ClassificationTask(
        column=column_name,
        prompt=prompt,
        model_name=model_name,
        label_num=label_num,
        valid_values=valid_values,
        temperature=temperature,
        q_name=q_name,
        once_verify_num=once_verify_num,
        max_verify_retry=max_verify_retry
    )

    # Classify and save the result
result_df_q3_first_try = gpt_classifier.classify_df(Q3_initial_sample, classification_task)
result_df_q3_first_try.to_excel("12_Q3_inital_sample_result.xlsx")



2023-09-19 17:34:23.511 | INFO     | gpt_classify_function:classify_df:175 - Classifying 1/200 Immigration Agents Raid Nearly 100 7-Eleven Stores Nationwide In Show Of Force
2023-09-19 17:34:25.553 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[1,1,0,0,0,0,0,0]', '[1,1,0,0,0,0,1,0]', '[1,1,0,0,0,0,0,0]']
2023-09-19 17:34:25.555 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1', '1', '0', '0', '0', '0', '0', '0'], ['1', '1', '0', '0', '0', '0', '1', '0'], ['1', '1', '0', '0', '0', '0', '0', '0']]
2023-09-19 17:34:25.556 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1_1_0_0_0_0_0_0', 2), ('1_1_0_0_0_0_1_0', 1)]
2023-09-19 17:34:25.557 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1_1_0_0_0_0_0_0 for Immigration Agents Raid Nearly 100 7-Eleven Stores Nationwide In Show Of Force
2023-09-19 17:34:25.563 | INFO     | gpt_classify_function:classify_df:175 - Classifying 2/200 DC forecast:

2023-09-19 17:34:40.417 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[0,0,0,0,0,1,0,0]', '[0,0,0,0,0,1,0,0]', '[0,0,0,0,0,1,0,0]']
2023-09-19 17:34:40.418 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 17:34:40.418 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_0_0', 3)]
2023-09-19 17:34:40.419 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_0_0 for Democrats Angry As Trump Restates Pro-American Immigration Principles
2023-09-19 17:34:40.422 | INFO     | gpt_classify_function:classify_df:175 - Classifying 9/200 Illegal Immigrant in San Francisco Killing Sentenced to Time Served on Weapons Charge
2023-09-19 17:34:42.342 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[0, 1, 0, 0, 0, 0, 1, 0]', '[0,1,0,0,0,0,0,0

2023-09-19 17:34:53.729 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[1,0,0,0,0,1,1,0]', '[1,0,0,0,0,1,0,0]', '[1,0,0,0,0,1,1,0]']
2023-09-19 17:34:53.730 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1', '0', '0', '0', '0', '1', '1', '0'], ['1', '0', '0', '0', '0', '1', '0', '0'], ['1', '0', '0', '0', '0', '1', '1', '0']]
2023-09-19 17:34:53.731 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1_0_0_0_0_1_1_0', 2), ('1_0_0_0_0_1_0_0', 1)]
2023-09-19 17:34:53.732 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1_0_0_0_0_1_1_0 for The Immigration Right Deal for the Dreamers — and the Nation
2023-09-19 17:34:53.738 | INFO     | gpt_classify_function:classify_df:175 - Classifying 16/200 Trump reaffirms promise of border wall before immigrations talks with Congress
2023-09-19 17:34:55.398 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[0,0,0,0,0,1,1,0]', '[0,0,0,0,0,1,0

2023-09-19 17:35:08.554 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0']]
2023-09-19 17:35:08.555 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_1_0', 3)]
2023-09-19 17:35:08.555 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_1_0 for Republican House Bill Exchanges DACA Amnesty for Mandatory E-Verify, Legal Immigration Cuts
2023-09-19 17:35:08.558 | INFO     | gpt_classify_function:classify_df:175 - Classifying 23/200 President Trump suggests 2-phase immigration deal for 'Dreamers'
2023-09-19 17:35:10.294 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[0,0,0,0,0,1,1,0]', '[0,0,0,0,0,1,1,0]', '[0,0,0,0,0,1,1,0]']
2023-09-19 17:35:10.294 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '1', '0'],

2023-09-19 17:35:19.541 | INFO     | gpt_classify_function:classify_df:175 - Classifying 30/200 Republican, Democrat Clash on Whether Immigration Deal Reached
2023-09-19 17:35:21.792 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[0,0,0,0,0,1,0,0]', '[0,0,0,0,0,1,0,0]', '[0, 0, 0, 0, 0, 1, 0, 0]']
2023-09-19 17:35:21.794 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 17:35:21.795 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_0_0', 3)]
2023-09-19 17:35:21.795 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_0_0 for Republican, Democrat Clash on Whether Immigration Deal Reached
2023-09-19 17:35:21.799 | INFO     | gpt_classify_function:classify_df:175 - Classifying 31/200 DHS chief says Trump would consider immigration legislation

...

2023-09-19 17:40:18.540 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_0_0', 3)]
2023-09-19 17:40:18.541 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_0_0 for Michelle Malkin on What She Wants to See in 2018: 'The Wall, the Wall, the Wall' - Breitbart
2023-09-19 17:40:18.546 | INFO     | gpt_classify_function:classify_df:175 - Classifying 171/200 Trump Administration Seeks $18 Billion Over Decade to Expand Border Wall
2023-09-19 17:40:20.282 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[0,0,0,0,0,1,1,0]', '[0,0,0,0,0,1,1,0]', '[0, 0, 0, 0, 0, 1, 1, 0]']
2023-09-19 17:40:20.283 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0']]
2023-09-19 17:40:20.284 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0

2023-09-19 17:40:32.775 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[1,0,0,0,0,1,0,0]', '[1,0,0,0,0,0,0,0]', '[1,0,0,0,0,1,0,0]']
2023-09-19 17:40:32.776 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1', '0', '0', '0', '0', '1', '0', '0'], ['1', '0', '0', '0', '0', '0', '0', '0'], ['1', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 17:40:32.777 | INFO     | gpt_classify_function:multi_verify:159 - Try:3 Sorted classifications: [('1_0_0_0_0_1_0_0', 2), ('1_0_0_0_0_0_0_0', 1)]
2023-09-19 17:40:32.778 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:3 Verified as 1_0_0_0_0_1_0_0 for Building the wall would be so worth it
2023-09-19 17:40:32.784 | INFO     | gpt_classify_function:classify_df:175 - Classifying 177/200 Trump comments highlight racial impact of migration platform
2023-09-19 17:40:35.129 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[0,0,0,0,0,1,0,0]', '[0,0,0,0,0,1,0,0]', '[0,0,0,0,1,1,0,0]']
2023-09-19 1

2023-09-19 17:40:43.228 | INFO     | gpt_classify_function:classify_df:175 - Classifying 184/200 Donald Trump reiterates support for ‘merit based’ immigration
2023-09-19 17:40:44.687 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[0,0,0,0,0,1,0,0]', '[0,0,0,0,0,1,0,0]', '[0,0,0,0,0,1,0,0]']
2023-09-19 17:40:44.688 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 17:40:44.690 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_0_0', 3)]
2023-09-19 17:40:44.691 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_0_0 for Donald Trump reiterates support for ‘merit based’ immigration
2023-09-19 17:40:44.697 | INFO     | gpt_classify_function:classify_df:175 - Classifying 185/200 Homeland chief: Wait and see on citizenship for immigrants
2023-09

2023-09-19 17:40:57.045 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '1', '0', '1', '0', '0'], ['0', '0', '0', '1', '0', '1', '0', '0'], ['0', '0', '0', '1', '0', '1', '0', '0']]
2023-09-19 17:40:57.046 | INFO     | gpt_classify_function:multi_verify:159 - Try:2 Sorted classifications: [('0_0_0_1_0_1_0_0', 3)]
2023-09-19 17:40:57.047 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:2 Verified as 0_0_0_1_0_1_0_0 for Trump administration's new immigration decision is shortsighted and cruel
2023-09-19 17:40:57.053 | INFO     | gpt_classify_function:classify_df:175 - Classifying 192/200 Trump's deportation czar threatens sanctuary city leaders with criminal charges, increased raids
2023-09-19 17:40:58.681 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[1,1,0,0,0,1,1,0]', '[0,1,0,0,0,1,0,0]', '[0,1,0,0,0,1,1,0]']
2023-09-19 17:40:58.683 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1', '1', '0', '0', '0', 

2023-09-19 17:41:12.098 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_0_0', 3)]
2023-09-19 17:41:12.099 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_0_0 for The Memo: Immigration battle tests activists’ muscle
2023-09-19 17:41:12.104 | INFO     | gpt_classify_function:classify_df:175 - Classifying 198/200 Border Patrol President: Because Of Trump ‘2018 Is Shaping Up To Be A Great Year’
2023-09-19 17:41:14.144 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ['[<0>,<0>,<0>,<0>,<0>,<1>,<0>,<0>]', '[0,0,0,0,0,1,0,0]', '[0, 0, 0, 0, 0, 1, 0, 0]']
2023-09-19 17:41:14.145 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 17:41:14.147 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_0_0', 

In [ ]:
# check if any colomn has error or can not converge after the max_verify_retry that needs human validation
review_human_validation_rows(df=result_df_q3_first_try, text_column="Post_Title", 
                                        valid_values= ['0', '1'] ,  
                                        classification_columns=["Q3_1_classification","Q3_2_classification","Q3_3_classification","Q3_4_classification","Q3_5_classification","Q3_6_classification","Q3_7_classification","Q3_8_classification"])


In [27]:
# caculate accuarcy
accuracies = {}

for i in range(1, 9):  # Loop from 2 to 8
    predict_col = f"Q3_{i}_classification"
    actual_col = f"Q3_{i}"
    
    accuracy = compute_accuracy(df=result_df_q3_first_try, 
                                predict_cols=[predict_col], 
                                actual_cols=[actual_col])
    
    accuracies[actual_col] = accuracy

# Print the accuracies
for col, acc in accuracies.items():
    print(f"Accuracy for {col}: {acc}")


Accuracy for Q3_1: 0.9
Accuracy for Q3_2: 0.935
Accuracy for Q3_3: 0.985
Accuracy for Q3_4: 0.84
Accuracy for Q3_5: 0.95
Accuracy for Q3_6: 0.85
Accuracy for Q3_7: 0.68
Accuracy for Q3_8: 0.94


Accrucy for Q7 is kind low, Finetune needed.

In [28]:
# finetune the df to train GPT
prepare_finetune_data(df=result_df_q3_first_try, 
                      text_column= "Post_Title", 
                      num_dimensions=8, 
                      column_names=['Q3_1','Q3_2','Q3_3', 'Q3_4', 'Q3_5', 'Q3_6','Q3_7', 'Q3_8'], 
                      prompt=prompt_Q3, 
                      output_file_name="13_Q3_finetune_1.jsonl")
   

In [29]:
# upload the Fine-tune dataset
finetune_file_Q3_1 = openai.File.create(
    file=open("13_Q3_finetune_1.jsonl", "rb"),
    purpose='fine-tune'
)
finetune_file_Q3_1

<File file id=file-NHuBOAiGzWiTL6gbnaPLg3xX at 0x2a1c32200> JSON: {
  "object": "file",
  "id": "file-NHuBOAiGzWiTL6gbnaPLg3xX",
  "purpose": "fine-tune",
  "filename": "file",
  "bytes": 746147,
  "created_at": 1695163313,
  "status": "uploaded",
  "status_details": null
}

In [34]:
# process the Fine-tune 
### It is normal to see an error saying that the id is not ready yet; just wait several minutes and allow OpenAI to process the result
finetune_file_Q3_1 = openai.FineTuningJob.create(
    training_file=finetune_file_Q3_1.id,
    model="gpt-3.5-turbo"
)
### This step usually takes several hours, depending on the capacity of OpenAI, and the number of assignment before
### You will received an email from OpenAI saying that the finetune job is done
### After process, when runing the "fine_tuning_job" you will see "  "trained_tokens": XXXX (instead of null)"

In [35]:
openai.FineTuningJob.retrieve(finetune_file_Q3_1.id) #Example of unfinised finetune work; the trained_tokkens is null

<FineTuningJob fine_tuning.job id=ftjob-8yxV2GiR1J1hyPLJYuWhezxD at 0x2a1c03380> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-8yxV2GiR1J1hyPLJYuWhezxD",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1695163374,
  "finished_at": null,
  "fine_tuned_model": null,
  "organization_id": "org-oC4UJKgkigzBaVPzhCPROXBW",
  "result_files": [],
  "status": "running",
  "validation_file": null,
  "training_file": "file-NHuBOAiGzWiTL6gbnaPLg3xX",
  "hyperparameters": {
    "n_epochs": 3
  },
  "trained_tokens": null,
  "error": null
}

In [38]:
openai.FineTuningJob.retrieve(finetune_file_Q3_1.id) #Example of finised finetune work; the trained_tokkens is not null

<FineTuningJob fine_tuning.job id=ftjob-8yxV2GiR1J1hyPLJYuWhezxD at 0x28d29bd80> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-8yxV2GiR1J1hyPLJYuWhezxD",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1695163374,
  "finished_at": 1695164578,
  "fine_tuned_model": "ft:gpt-3.5-turbo-0613:jcs-research::80e27Roc",
  "organization_id": "org-oC4UJKgkigzBaVPzhCPROXBW",
  "result_files": [
    "file-IH4EDsY96QGhq6Dku2JCQE6q"
  ],
  "status": "succeeded",
  "validation_file": null,
  "training_file": "file-NHuBOAiGzWiTL6gbnaPLg3xX",
  "hyperparameters": {
    "n_epochs": 3
  },
  "trained_tokens": 423309,
  "error": null
}

In [39]:
gpt_fintuned_Q3_1 = openai.FineTuningJob.retrieve(finetune_file_Q3_1.id).fine_tuned_model 
gpt_fintuned_Q3_1

'ft:gpt-3.5-turbo-0613:jcs-research::80e27Roc'

In [40]:
# sample another 200 post and get the classfication result from the finetuned model
df_remaining = train_df_yes_immigration.drop(Q3_initial_sample.index)
Q3_second_sample = df_remaining.sample(SAMPLE_SIZE, random_state=SEED)
Q3_second_sample.to_excel("14_Q3_second_sample.xlsx")
Q3_second_sample

ID  ID_original                                  GUID  \
1431  1433         6645  f66f5de8-42ba-4eb3-8a51-2dd0d4b41d48   
544    545         2666  60c45290-9acd-4210-8116-32519d850157   
5        6           25  8524c992-f1a8-4a2b-9cc8-55cbab86072d   
687    688         3380  65a596b9-da4d-4fad-bf81-34ca04bcaad0   
1273  1274         5901  e0faa896-75a9-4319-a0c1-90e201cdd5bf   
...    ...          ...                                   ...   
1056  1057         5045  dbdad1fa-5081-4a70-bcae-5fe27332d0c9   
771    772         3767  e945cd8f-860f-46a8-a073-361c3799831a   
1172  1173         5543  b2379b68-6ac9-4023-9295-001de83843cf   
1339  1341         6184  14b663c0-5e7e-4ec5-b17d-2ce117bf6d88   
1995  1997          491  0aaa0986-a0d7-4e0b-8ce5-fb11f1bd096d   

              Date (GMT)                                                URL  \
1431 2018-01-11 04:05:44  https://www.washingtonpost.com/politics/courts...   
544  2018-01-09 19:06:13  http://www.motherjones.com/kevin-drum/2018/01/...   
5    2018-01-11 10:47:57  http://www.yahoo.com/news/lawmakers-renew-immi...   
687  2018-01-10 06:34:15  http://www.cnn.com/transcripts/1801/09/wolf.01...   
1273 2018-01-02 00:00:00  https://www.yahoo.com/news/m/913b1b66-642d-3ff...   
...                  ...                                                ...   
1056 2018-01-11 13:43:27  https://www.yahoo.com/news/immigration-agents-...   
771  2018-01-04 15:13:53  http://thehill.com/opinion/immigration/367371-...   
1172 2018-01-11 11:32:26  http://www.foxnews.com/us/2018/01/11/fox-news-...   
1339 2018-01-12 06:28:12  https://www.usatoday.com/story/news/politics/o...   
1995 2018-01-28 00:03:22  http://thehill.com/latino/370872-five-hurdles-...   

                                             Post_Title Q1 Q2  Q3_1_og  \
1431  The Latest: Bipartisan lawmakers begin immigra...  1  2      6.0   
544   Trump: I’ll Sign Any Immigration Bill Congress...  1  2      6.0   
5     Growing pressure on both sides for immigration...  1  2      6.0   
687   Bipartisan Immigration Bill Roundtable. Aired ...  1  2      7.0   
1273  Acting ICE director wants to ignore Constituti...  1  2      2.0   
...                                                 ... .. ..      ...   
1056  Immigration Agents Raid Nearly 100 7-Eleven St...  1  2      1.0   
771   If California has power to defy immigration la...  1  2      7.0   
1172  FOX NEWS FIRST: Grammy winner blasts Oprah for...  1  2      8.0   
1339  &apos;Divisive,&apos; &apos;elitist,&apos; &ap...  1  2      4.0   
1995        Five hurdles to getting an immigration deal  1  2      7.0   

      Q3_2_og Train Q3_1 Q3_2 Q3_3 Q3_4 Q3_5 Q3_6 Q3_7 Q3_8  
1431     99.0     1    0    0    0    0    0    1    0    0  
544       7.0     1    0    0    0    0    0    1    1    0  
5         7.0     1    0    0    0    0    0    1    1    0  
687      99.0     1    0    0    0    0    0    0    1    0  
1273     99.0     1    0    1    0    0    0    0    0    0  
...       ...   ...  ...  ...  ...  ...  ...  ...  ...  ...  
1056      2.0     1    1    1    0    0    0    0    0    0  
771      99.0     1    0    0    0    0    0    0    1    0  
1172      7.0     1    0    0    0    0    0    0    1    1  
1339      6.0     1    0    0    0    1    0    1    0    0  
1995     99.0     1    0    0    0    0    0    0    1    0  

[200 rows x 19 columns]

In [41]:
# Q3 second sample after fine-tune
if __name__ == "__main__":
    # Setup parameters
    column_name = "Post_Title"  # the column name for the text to be classified
    model_name = gpt_fintuned_Q3_1  # the GPT model to use
    label_num = 8  # the number of dimensions of this variable
    valid_values = ['0', '1']  # the valid answers from this question
    temperature = 0.7  # temperature 
    q_name = "Q3"  # the name of this question/variable
    once_verify_num = 3  # the numbers of results generated from GPT 
    max_verify_retry = 5  # the number of retries if the previous is not converged

    # Prompt setup
prompt =  prompt_Q3

    # Initialize GPT Classifier
gpt_classifier = GPTClassifier()

    # Setup classification task
classification_task = ClassificationTask(
        column=column_name,
        prompt=prompt,
        model_name=model_name,
        label_num=label_num,
        valid_values=valid_values,
        temperature=temperature,
        q_name=q_name,
        once_verify_num=once_verify_num,
        max_verify_retry=max_verify_retry
    )

    # Classify and save the result
result_df_q3_second_try = gpt_classifier.classify_df(Q3_second_sample, classification_task)
result_df_q3_second_try.to_excel("15_Q3_second_sample_result.xlsx")


2023-09-19 18:06:12.915 | INFO     | gpt_classify_function:classify_df:175 - Classifying 1/200 The Latest: Bipartisan lawmakers begin immigration effort


Request timed out. Retrying...
Request timed out. Retrying...


2023-09-19 18:06:30.279 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '1', '1', '0']", "['0', '0', '0', '0', '0', '1', '1', '0']", "['0', '0', '0', '0', '0', '1', '1', '0']"]
2023-09-19 18:06:30.279 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0']]
2023-09-19 18:06:30.280 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_1_0', 3)]
2023-09-19 18:06:30.280 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_1_0 for The Latest: Bipartisan lawmakers begin immigration effort
2023-09-19 18:06:30.285 | INFO     | gpt_classify_function:classify_df:175 - Classifying 2/200 Trump: I’ll Sign Any Immigration Bill Congress Sends Me
2023-09-19 18:06:30.891 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '

Request timed out. Retrying...


2023-09-19 18:06:39.294 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '0', '1', '0']", "['0', '0', '0', '0', '0', '0', '1', '0']", "['0', '0', '0', '0', '0', '0', '1', '0']"]
2023-09-19 18:06:39.295 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '0', '1', '0'], ['0', '0', '0', '0', '0', '0', '1', '0'], ['0', '0', '0', '0', '0', '0', '1', '0']]
2023-09-19 18:06:39.296 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_0_1_0', 3)]
2023-09-19 18:06:39.296 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_0_1_0 for Bipartisan Immigration Bill Roundtable. Aired 1-1:30p ET
2023-09-19 18:06:39.299 | INFO     | gpt_classify_function:classify_df:175 - Classifying 5/200 Acting ICE director wants to ignore Constitution, arrest local leaders for sanctuary city policies
2023-09-19 18:06:40.006 | DEBUG    | gpt_classify_function:class

...

2023-09-19 18:08:29.483 | INFO     | gpt_classify_function:classify_df:175 - Classifying 172/200 Ted Lieu to Trump: I support an immigration system like the one your grandfather used to come to US
2023-09-19 18:08:30.089 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '1', '1', '0']", "['0', '0', '0', '0', '0', '1', '1', '0']", "['0', '0', '0', '0', '0', '1', '1', '0']"]
2023-09-19 18:08:30.090 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0']]
2023-09-19 18:08:30.091 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_1_0', 3)]
2023-09-19 18:08:30.092 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_1_0 for Ted Lieu to Trump: I support an immigration system like the one your grandfather used to come to US
2023-09-19 18:08:3

2023-09-19 18:08:33.465 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1', '0', '0', '0', '0', '1', '0', '0'], ['1', '0', '0', '0', '0', '1', '0', '0'], ['1', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 18:08:33.467 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1_0_0_0_0_1_0_0', 3)]
2023-09-19 18:08:33.467 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1_0_0_0_0_1_0_0 for Trump administration proposes $18 billion wall bordering Mexico
2023-09-19 18:08:33.473 | INFO     | gpt_classify_function:classify_df:175 - Classifying 180/200 Unraveling The Mystery Of How A Border Patrol Agent Died In West Texas
2023-09-19 18:08:34.082 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '1', '0', '0', '0', '0', '0', '0']", "['0', '1', '0', '0', '0', '0', '0', '0']", "['0', '1', '0', '0', '0', '0', '0', '0']"]
2023-09-19 18:08:34.083 | DEBUG    | gpt_classify_function:classify:139 - Valid res

2023-09-19 18:08:37.666 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '1', '0', '0']", "['0', '0', '0', '0', '0', '1', '0', '0']", "['0', '0', '0', '0', '0', '1', '0', '0']"]
2023-09-19 18:08:37.667 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 18:08:37.668 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_0_0', 3)]
2023-09-19 18:08:37.669 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_0_0 for Trump’s Negotiation on Immigration, Unfolding on Camera
2023-09-19 18:08:37.675 | INFO     | gpt_classify_function:classify_df:175 - Classifying 187/200 Illegal immigrant acquitted in California death gets prison on gun charge
2023-09-19 18:08:38.200 | DEBUG    | gpt_classify_function:classify:119 - Raw results: [

2023-09-19 18:08:40.978 | INFO     | gpt_classify_function:classify_df:175 - Classifying 193/200 'Door of Hope' is closed to cross-border hugs and weddings - LA Times
2023-09-19 18:08:41.500 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '0', '0', '1']", "['0', '0', '0', '0', '0', '0', '0', '1']", "['0', '0', '0', '0', '0', '0', '0', '1']"]
2023-09-19 18:08:41.502 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '0', '0', '1'], ['0', '0', '0', '0', '0', '0', '0', '1'], ['0', '0', '0', '0', '0', '0', '0', '1']]
2023-09-19 18:08:41.503 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_0_0_1', 3)]
2023-09-19 18:08:41.504 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_0_0_1 for 'Door of Hope' is closed to cross-border hugs and weddings - LA Times
2023-09-19 18:08:41.509 | INFO     | gpt_classify_function:classify_df:175 - C

2023-09-19 18:08:45.348 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_1_0_1_0_1', 3)]
2023-09-19 18:08:45.349 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_1_0_1_0_1 for &apos;Divisive,&apos; &apos;elitist,&apos; &apos;racist&apos;: Reactions to Trump&apos;s immigration comments
2023-09-19 18:08:45.355 | INFO     | gpt_classify_function:classify_df:175 - Classifying 200/200 Five hurdles to getting an immigration deal
2023-09-19 18:08:45.852 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '0', '1', '0']", "['0', '0', '0', '0', '0', '0', '1', '0']", "['0', '0', '0', '0', '0', '0', '1', '0']"]
2023-09-19 18:08:45.853 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '0', '1', '0'], ['0', '0', '0', '0', '0', '0', '1', '0'], ['0', '0', '0', '0', '0', '0', '1', '0']]
2023-09-19 18:08:45.854 | INFO     | gpt_classify_function:multi

In [42]:
# check if any colomn has error or can not converge after the max_verify_retry that needs human validation
review_human_validation_rows(df=result_df_q3_second_try, text_column="Post_Title", 
                                        valid_values= ['0', '1'] ,  
                                        classification_columns=['Q3_1', 'Q3_2','Q3_3', 'Q3_4', 'Q3_5', 'Q3_6','Q3_7', 'Q3_8'])


No row needs human validation, please proceed


ID  ID_original                                  GUID  \
0    1433         6645  f66f5de8-42ba-4eb3-8a51-2dd0d4b41d48   
1     545         2666  60c45290-9acd-4210-8116-32519d850157   
2       6           25  8524c992-f1a8-4a2b-9cc8-55cbab86072d   
3     688         3380  65a596b9-da4d-4fad-bf81-34ca04bcaad0   
4    1274         5901  e0faa896-75a9-4319-a0c1-90e201cdd5bf   
..    ...          ...                                   ...   
195  1057         5045  dbdad1fa-5081-4a70-bcae-5fe27332d0c9   
196   772         3767  e945cd8f-860f-46a8-a073-361c3799831a   
197  1173         5543  b2379b68-6ac9-4023-9295-001de83843cf   
198  1341         6184  14b663c0-5e7e-4ec5-b17d-2ce117bf6d88   
199  1997          491  0aaa0986-a0d7-4e0b-8ce5-fb11f1bd096d   

             Date (GMT)                                                URL  \
0   2018-01-11 04:05:44  https://www.washingtonpost.com/politics/courts...   
1   2018-01-09 19:06:13  http://www.motherjones.com/kevin-drum/2018/01/...   
2   2018-01-11 10:47:57  http://www.yahoo.com/news/lawmakers-renew-immi...   
3   2018-01-10 06:34:15  http://www.cnn.com/transcripts/1801/09/wolf.01...   
4   2018-01-02 00:00:00  https://www.yahoo.com/news/m/913b1b66-642d-3ff...   
..                  ...                                                ...   
195 2018-01-11 13:43:27  https://www.yahoo.com/news/immigration-agents-...   
196 2018-01-04 15:13:53  http://thehill.com/opinion/immigration/367371-...   
197 2018-01-11 11:32:26  http://www.foxnews.com/us/2018/01/11/fox-news-...   
198 2018-01-12 06:28:12  https://www.usatoday.com/story/news/politics/o...   
199 2018-01-28 00:03:22  http://thehill.com/latino/370872-five-hurdles-...   

                                            Post_Title Q1 Q2  Q3_1_og  \
0    The Latest: Bipartisan lawmakers begin immigra...  1  2      6.0   
1    Trump: I’ll Sign Any Immigration Bill Congress...  1  2      6.0   
2    Growing pressure on both sides for immigration...  1  2      6.0   
3    Bipartisan Immigration Bill Roundtable. Aired ...  1  2      7.0   
4    Acting ICE director wants to ignore Constituti...  1  2      2.0   
..                                                 ... .. ..      ...   
195  Immigration Agents Raid Nearly 100 7-Eleven St...  1  2      1.0   
196  If California has power to defy immigration la...  1  2      7.0   
197  FOX NEWS FIRST: Grammy winner blasts Oprah for...  1  2      8.0   
198  &apos;Divisive,&apos; &apos;elitist,&apos; &ap...  1  2      4.0   
199        Five hurdles to getting an immigration deal  1  2      7.0   

     Q3_2_og  ... Q3_7 Q3_8 Q3_1_classification Q3_2_classification  \
0       99.0  ...    0    0                   0                   0   
1        7.0  ...    1    0                   0                   0   
2        7.0  ...    1    0                   0                   0   
3       99.0  ...    1    0                   0                   0   
4       99.0  ...    0    0                   0                   0   
..       ...  ...  ...  ...                 ...                 ...   
195      2.0  ...    0    0                   1                   0   
196     99.0  ...    1    0                   0                   0   
197      7.0  ...    1    1                   0                   0   
198      6.0  ...    0    0                   0                   0   
199     99.0  ...    1    0                   0                   0   

    Q3_3_classification Q3_4_classification Q3_5_classification  \
0                     0                   0                   0   
1                     0                   0                   0   
2                     0                   0                   0   
3                     0                   0                   0   
4                     0                   0                   0   
..                  ...                 ...                 ...   
195                   0                   0                   0   
196                   0            

In [43]:
# caculate accuarcy
accuracies = {}

for i in range(1, 9):  # Loop from 2 to 8
    predict_col = f"Q3_{i}_classification"
    actual_col = f"Q3_{i}"
    
    accuracy = compute_accuracy(df=result_df_q3_second_try, 
                                predict_cols=[predict_col], 
                                actual_cols=[actual_col])
    
    accuracies[actual_col] = accuracy

# Print the accuracies
for col, acc in accuracies.items():
    print(f"Accuracy for {col}: {acc}")


Accuracy for Q3_1: 0.95
Accuracy for Q3_2: 0.92
Accuracy for Q3_3: 0.985
Accuracy for Q3_4: 0.87
Accuracy for Q3_5: 0.98
Accuracy for Q3_6: 0.885
Accuracy for Q3_7: 0.86
Accuracy for Q3_8: 0.93


In [46]:
# q7 is kind okay but still low. Needs more validation
# We will combine the first two validets sample (N=400) as finetune
result_df_q3_first_second_try = pd.concat([result_df_q3_first_try, result_df_q3_second_try])
# finetune the df to train GPT
prepare_finetune_data(df=result_df_q3_first_second_try, 
                      text_column= "Post_Title", 
                      num_dimensions=8, 
                      column_names=['Q3_1','Q3_2','Q3_3', 'Q3_4', 'Q3_5', 'Q3_6','Q3_7', 'Q3_8'], 
                      prompt=prompt_Q3, 
                      output_file_name="16_Q3_finetune_2.jsonl")
   

In [47]:
# upload the Fine-tune dataset
finetune_file_Q3_2 = openai.File.create(
    file=open("16_Q3_finetune_2.jsonl", "rb"),
    purpose='fine-tune'
)
finetune_file_Q3_2

<File file id=file-MGqm93G22zUIzAOxyaNsrpBB at 0x28d018310> JSON: {
  "object": "file",
  "id": "file-MGqm93G22zUIzAOxyaNsrpBB",
  "purpose": "fine-tune",
  "filename": "file",
  "bytes": 1491887,
  "created_at": 1695165319,
  "status": "uploaded",
  "status_details": null
}

In [66]:
# process the Fine-tune 
### It is normal to see an error saying that the id is not ready yet; just wait several minutes and allow OpenAI to process the result
finetune_file_Q3_2 = openai.FineTuningJob.create(
    training_file=finetune_file_Q3_2.id,
    model="gpt-3.5-turbo"
)
### This step usually takes several hours, depending on the capacity of OpenAI, and the number of assignment before
### You will received an email from OpenAI saying that the finetune job is done
### After process, when runing the "fine_tuning_job" you will see "  "trained_tokens": XXXX (instead of null)"

In [69]:
openai.FineTuningJob.retrieve(finetune_file_Q3_2.id)

<FineTuningJob fine_tuning.job id=ftjob-JxsecZmmbI7QpQvHcMIcjKGA at 0x28d39cef0> JSON: {
  "object": "fine_tuning.job",
  "id": "ftjob-JxsecZmmbI7QpQvHcMIcjKGA",
  "model": "gpt-3.5-turbo-0613",
  "created_at": 1695165945,
  "finished_at": 1695167964,
  "fine_tuned_model": "ft:gpt-3.5-turbo-0613:jcs-research::80euj08r",
  "organization_id": "org-oC4UJKgkigzBaVPzhCPROXBW",
  "result_files": [
    "file-ZDWHf6C3XpMhSV0nOzQhzuLe"
  ],
  "status": "succeeded",
  "validation_file": null,
  "training_file": "file-MGqm93G22zUIzAOxyaNsrpBB",
  "hyperparameters": {
    "n_epochs": 3
  },
  "trained_tokens": 846555,
  "error": null
}

In [70]:
gpt_fintuned_Q3_2 = openai.FineTuningJob.retrieve(finetune_file_Q3_2.id).fine_tuned_model 
gpt_fintuned_Q3_2

'ft:gpt-3.5-turbo-0613:jcs-research::80euj08r'

In [71]:
# sample another 200 post and get the classfication result from the finetuned model
df_remaining_2 = df_remaining.drop(Q3_second_sample.index)
Q3_third_sample = df_remaining.sample(SAMPLE_SIZE, random_state=SEED)
Q3_third_sample.to_excel("17_Q3_third_sample.xlsx")


In [73]:
# Q3 third sample after fine-tune
if __name__ == "__main__":
    # Setup parameters
    column_name = "Post_Title"  # the column name for the text to be classified
    model_name = gpt_fintuned_Q3_2  # the GPT model to use
    label_num = 8  # the number of dimensions of this variable
    valid_values = ['0', '1']  # the valid answers from this question
    temperature = 0.7  # temperature 
    q_name = "Q3"  # the name of this question/variable
    once_verify_num = 3  # the numbers of results generated from GPT 
    max_verify_retry = 5  # the number of retries if the previous is not converged

    # Prompt setup
prompt =  prompt_Q3

    # Initialize GPT Classifier
gpt_classifier = GPTClassifier()

    # Setup classification task
classification_task = ClassificationTask(
        column=column_name,
        prompt=prompt,
        model_name=model_name,
        label_num=label_num,
        valid_values=valid_values,
        temperature=temperature,
        q_name=q_name,
        once_verify_num=once_verify_num,
        max_verify_retry=max_verify_retry
    )

    # Classify and save the result
result_df_q3_third_try = gpt_classifier.classify_df(Q3_third_sample, classification_task)
result_df_q3_third_try.to_excel("18_Q3_third_sample_result.xlsx")


2023-09-19 19:15:48.549 | INFO     | gpt_classify_function:classify_df:175 - Classifying 1/200 The Latest: Bipartisan lawmakers begin immigration effort
2023-09-19 19:15:48.551 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '0', '1', '0'] The Latest: Bipartisan lawmakers begin immigration effort
2023-09-19 19:15:48.551 | INFO     | gpt_classify_function:classify_df:175 - Classifying 2/200 Trump: I’ll Sign Any Immigration Bill Congress Sends Me
2023-09-19 19:15:48.553 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '1', '1', '0'] Trump: I’ll Sign Any Immigration Bill Congress Sends Me
2023-09-19 19:15:48.554 | INFO     | gpt_classify_function:classify_df:175 - Classifying 3/200 Growing pressure on both sides for immigration deal
2023-09-19 19:15:48.555 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '0', '1', '0'] Growing pressure on both sides for immigration d

2023-09-19 19:15:48.579 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '1', '0', '0'] AP FACT CHECK: Trump hypes claims on immigrants, TV viewers
2023-09-19 19:15:48.580 | INFO     | gpt_classify_function:classify_df:175 - Classifying 20/200 Report: Trump uses crude term while attacking protections for immigrants
2023-09-19 19:15:48.581 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '1', '0', '1', '0', '0'] Report: Trump uses crude term while attacking protections for immigrants
2023-09-19 19:15:48.581 | INFO     | gpt_classify_function:classify_df:175 - Classifying 21/200 100 7-Eleven Stores Hit With Pre-Dawn Immigration Raids
2023-09-19 19:15:48.582 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1', '0', '0', '0', '0', '0', '0', '0'] 100 7-Eleven Stores Hit With Pre-Dawn Immigration Raids
2023-09-19 19:15:48.582 | INFO     | gpt_classify_function:classify_df:175 - Classifying 22/200 Border 

2023-09-19 19:15:48.599 | INFO     | gpt_classify_function:classify_df:175 - Classifying 37/200 These Claims About ‘Chain Migration’ Are Not Accurate
2023-09-19 19:15:48.600 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '0', '0', '0'] These Claims About ‘Chain Migration’ Are Not Accurate
2023-09-19 19:15:48.600 | INFO     | gpt_classify_function:classify_df:175 - Classifying 38/200 Factbox: Trump on Twitter (January 10)-U.S. Court System, Feinstein, Border Wall
2023-09-19 19:15:48.601 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '1', '1', '0'] Factbox: Trump on Twitter (January 10)-U.S. Court System, Feinstein, Border Wall
2023-09-19 19:15:48.601 | INFO     | gpt_classify_function:classify_df:175 - Classifying 39/200 Trump: 'Mexico Will Pay for the Wall'
2023-09-19 19:15:48.602 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1', '0', '0', '0', '0', '1', '0', '0'] Trump: 'Mexico Wi

2023-09-19 19:15:48.619 | INFO     | gpt_classify_function:classify_df:175 - Classifying 55/200 Trump Administration Blocking Another Immigrant Woman From Getting An Abortion
2023-09-19 19:15:48.620 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '1', '0', '1', '0', '0'] Trump Administration Blocking Another Immigrant Woman From Getting An Abortion
2023-09-19 19:15:48.620 | INFO     | gpt_classify_function:classify_df:175 - Classifying 56/200 Border inspections of electronic devices hits record number
2023-09-19 19:15:48.621 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '1', '0', '0', '0', '0', '0', '0'] Border inspections of electronic devices hits record number
2023-09-19 19:15:48.621 | INFO     | gpt_classify_function:classify_df:175 - Classifying 57/200 Fake highway signs jab at new California immigration law
2023-09-19 19:15:48.622 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '0', 

2023-09-19 19:15:48.640 | INFO     | gpt_classify_function:classify_df:175 - Classifying 73/200 Report: Trump Upset That ‘People From S***hole’ Countries’ Immigrate To America
2023-09-19 19:15:48.641 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '1', '0', '1', '0', '0'] Report: Trump Upset That ‘People From S***hole’ Countries’ Immigrate To America
2023-09-19 19:15:48.641 | INFO     | gpt_classify_function:classify_df:175 - Classifying 74/200 Anderson Cooper, John Legend call Trump &apos;racist&apos; following immigration comments
2023-09-19 19:15:48.642 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '1', '0', '1', '0', '0'] Anderson Cooper, John Legend call Trump &apos;racist&apos; following immigration comments
2023-09-19 19:15:48.642 | INFO     | gpt_classify_function:classify_df:175 - Classifying 75/200 Trump, Republicans face immigration reckoning
2023-09-19 19:15:48.643 | INFO     | gpt_classify_function:multi_ver

...

2023-09-19 19:15:48.698 | INFO     | gpt_classify_function:classify_df:175 - Classifying 126/200 Trump's comments make things more difficult for groups that want to limit immigration
2023-09-19 19:15:48.699 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '1', '0', '0'] Trump's comments make things more difficult for groups that want to limit immigration
2023-09-19 19:15:48.699 | INFO     | gpt_classify_function:classify_df:175 - Classifying 127/200 A year into Trump's presidency, the media is still ignorant of his plan for a wall | TheHill
2023-09-19 19:15:48.700 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '1', '1', '0'] A year into Trump's presidency, the media is still ignorant of his plan for a wall | TheHill
2023-09-19 19:15:48.700 | INFO     | gpt_classify_function:classify_df:175 - Classifying 128/200 These Claims About ‘Chain Migration’ Are Not Accurate
2023-09-19 19:15:48.701 | INFO     | gp

2023-09-19 19:15:48.715 | INFO     | gpt_classify_function:classify_df:175 - Classifying 144/200 Prank California highway signs 'welcome' felons, illegal immigrants and MS-13
2023-09-19 19:15:48.716 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '1', '0', '0', '0', '0', '0', '0'] Prank California highway signs 'welcome' felons, illegal immigrants and MS-13
2023-09-19 19:15:48.716 | INFO     | gpt_classify_function:classify_df:175 - Classifying 145/200 Trump's Anti-Immigration Rhetoric, Policies Killing Tourism to the U.S., Industry Analysts Say
2023-09-19 19:15:48.717 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1', '0', '0', '0', '0', '1', '0', '0'] Trump's Anti-Immigration Rhetoric, Policies Killing Tourism to the U.S., Industry Analysts Say
2023-09-19 19:15:48.717 | INFO     | gpt_classify_function:classify_df:175 - Classifying 146/200 Bernie Sanders Claims ‘No One Wants’ A Border Wall
2023-09-19 19:15:48.718 | INFO     | gpt_classify_func

2023-09-19 19:15:48.733 | INFO     | gpt_classify_function:classify_df:175 - Classifying 161/200 Trump’s Vulgar Immigration Remarks Alarm Lawmakers
2023-09-19 19:15:48.734 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '1', '0', '1', '0', '0'] Trump’s Vulgar Immigration Remarks Alarm Lawmakers
2023-09-19 19:15:48.735 | INFO     | gpt_classify_function:classify_df:175 - Classifying 162/200 APNewsBreak: 7-Eleven Probe Opens New Front on Immigration
2023-09-19 19:15:48.735 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1', '0', '0', '0', '0', '0', '0', '0'] APNewsBreak: 7-Eleven Probe Opens New Front on Immigration
2023-09-19 19:15:48.736 | INFO     | gpt_classify_function:classify_df:175 - Classifying 163/200 Trump Open to Talks with North; Boardroom Trump verses Cabinet Room Trump; Jones Diagnosed with Leukemia; Physical Wall for Border. Aired 6:30-7:00a ET
2023-09-19 19:15:48.737 | INFO     | gpt_classify_function:multi_verify:144 - C

2023-09-19 19:15:48.751 | INFO     | gpt_classify_function:classify_df:175 - Classifying 178/200 Fake highway signs jab at new California immigration law
2023-09-19 19:15:48.752 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '0', '1', '0'] Fake highway signs jab at new California immigration law
2023-09-19 19:15:48.752 | INFO     | gpt_classify_function:classify_df:175 - Classifying 179/200 Trump administration proposes $18 billion wall bordering Mexico
2023-09-19 19:15:48.753 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1', '0', '0', '0', '0', '1', '0', '0'] Trump administration proposes $18 billion wall bordering Mexico
2023-09-19 19:15:48.753 | INFO     | gpt_classify_function:classify_df:175 - Classifying 180/200 Unraveling The Mystery Of How A Border Patrol Agent Died In West Texas
2023-09-19 19:15:48.754 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '1', '0', '0', '0', '0', '0', '0'] Unravelin

2023-09-19 19:15:48.771 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '1', '0', '1', '0', '0'] Durbin: Term ‘Chain Migration’ Painful to African-Americans Because They Migrated to U.S. in Chains
2023-09-19 19:15:48.771 | INFO     | gpt_classify_function:classify_df:175 - Classifying 196/200 Immigration Agents Raid Nearly 100 7-Eleven Stores Nationwide In Show Of Force
2023-09-19 19:15:48.772 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['1', '0', '0', '0', '0', '0', '0', '0'] Immigration Agents Raid Nearly 100 7-Eleven Stores Nationwide In Show Of Force
2023-09-19 19:15:48.772 | INFO     | gpt_classify_function:classify_df:175 - Classifying 197/200 If California has power to defy immigration laws, could secede as well?
2023-09-19 19:15:48.773 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '0', '1', '0'] If California has power to defy immigration laws, could secede as well?
2023-09-19 19:15:

In [74]:
# check if any colomn has error or can not converge after the max_verify_retry that needs human validation
review_human_validation_rows(df=result_df_q3_third_try, text_column="Post_Title", 
                                        valid_values= ['0', '1'] ,  
                                        classification_columns=['Q3_1', 'Q3_2','Q3_3', 'Q3_4', 'Q3_5', 'Q3_6','Q3_7', 'Q3_8'])


No row needs human validation, please proceed


ID  ID_original                                  GUID  \
0    1433         6645  f66f5de8-42ba-4eb3-8a51-2dd0d4b41d48   
1     545         2666  60c45290-9acd-4210-8116-32519d850157   
2       6           25  8524c992-f1a8-4a2b-9cc8-55cbab86072d   
3     688         3380  65a596b9-da4d-4fad-bf81-34ca04bcaad0   
4    1274         5901  e0faa896-75a9-4319-a0c1-90e201cdd5bf   
..    ...          ...                                   ...   
195  1057         5045  dbdad1fa-5081-4a70-bcae-5fe27332d0c9   
196   772         3767  e945cd8f-860f-46a8-a073-361c3799831a   
197  1173         5543  b2379b68-6ac9-4023-9295-001de83843cf   
198  1341         6184  14b663c0-5e7e-4ec5-b17d-2ce117bf6d88   
199  1997          491  0aaa0986-a0d7-4e0b-8ce5-fb11f1bd096d   

             Date (GMT)                                                URL  \
0   2018-01-11 04:05:44  https://www.washingtonpost.com/politics/courts...   
1   2018-01-09 19:06:13  http://www.motherjones.com/kevin-drum/2018/01/...   
2   2018-01-11 10:47:57  http://www.yahoo.com/news/lawmakers-renew-immi...   
3   2018-01-10 06:34:15  http://www.cnn.com/transcripts/1801/09/wolf.01...   
4   2018-01-02 00:00:00  https://www.yahoo.com/news/m/913b1b66-642d-3ff...   
..                  ...                                                ...   
195 2018-01-11 13:43:27  https://www.yahoo.com/news/immigration-agents-...   
196 2018-01-04 15:13:53  http://thehill.com/opinion/immigration/367371-...   
197 2018-01-11 11:32:26  http://www.foxnews.com/us/2018/01/11/fox-news-...   
198 2018-01-12 06:28:12  https://www.usatoday.com/story/news/politics/o...   
199 2018-01-28 00:03:22  http://thehill.com/latino/370872-five-hurdles-...   

                                            Post_Title Q1 Q2  Q3_1_og  \
0    The Latest: Bipartisan lawmakers begin immigra...  1  2      6.0   
1    Trump: I’ll Sign Any Immigration Bill Congress...  1  2      6.0   
2    Growing pressure on both sides for immigration...  1  2      6.0   
3    Bipartisan Immigration Bill Roundtable. Aired ...  1  2      7.0   
4    Acting ICE director wants to ignore Constituti...  1  2      2.0   
..                                                 ... .. ..      ...   
195  Immigration Agents Raid Nearly 100 7-Eleven St...  1  2      1.0   
196  If California has power to defy immigration la...  1  2      7.0   
197  FOX NEWS FIRST: Grammy winner blasts Oprah for...  1  2      8.0   
198  &apos;Divisive,&apos; &apos;elitist,&apos; &ap...  1  2      4.0   
199        Five hurdles to getting an immigration deal  1  2      7.0   

     Q3_2_og  ... Q3_7 Q3_8 Q3_1_classification Q3_2_classification  \
0       99.0  ...    0    0                   0                   0   
1        7.0  ...    1    0                   0                   0   
2        7.0  ...    1    0                   0                   0   
3       99.0  ...    1    0                   0                   0   
4       99.0  ...    0    0                   0                   1   
..       ...  ...  ...  ...                 ...                 ...   
195      2.0  ...    0    0                   1                   0   
196     99.0  ...    1    0                   0                   0   
197      7.0  ...    1    1                   0                   0   
198      6.0  ...    0    0                   0                   0   
199     99.0  ...    1    0                   0                   0   

    Q3_3_classification Q3_4_classification Q3_5_classification  \
0                     0                   0                   0   
1                     0                   0                   0   
2                     0                   0                   0   
3                     0                   0                   0   
4                     0                   0                   0   
..                  ...                 ...                 ...   
195                   0                   0                   0   
196                   0            

In [75]:
# caculate accuarcy
accuracies = {}

for i in range(1, 9):  # Loop from 2 to 8
    predict_col = f"Q3_{i}_classification"
    actual_col = f"Q3_{i}"
    
    accuracy = compute_accuracy(df=result_df_q3_third_try, 
                                predict_cols=[predict_col], 
                                actual_cols=[actual_col])
    
    accuracies[actual_col] = accuracy

# Print the accuracies
for col, acc in accuracies.items():
    print(f"Accuracy for {col}: {acc}")


Accuracy for Q3_1: 0.975
Accuracy for Q3_2: 0.965
Accuracy for Q3_3: 0.99
Accuracy for Q3_4: 0.94
Accuracy for Q3_5: 0.995
Accuracy for Q3_6: 0.935
Accuracy for Q3_7: 0.915
Accuracy for Q3_8: 0.98


In [76]:
# The accuracy is good, work on the Q3 for the test df
# One more logic for Q3, if Q1 == 2, we will skip it and directly enter 99

# Filter out rows where Q1_1_classification is "2" and classify the remaining rows
filtered_df = test_df[test_df['Q1_1_classification'] == "1"]
filtered_df.to_excel("18_Q3_third_sample_result.xlsx")


In [77]:
if __name__ == "__main__":
    # Setup parameters
    column_name = "Post_Title"  # the column name for the text to be classified
    model_name = gpt_fintuned_Q3_2  # the GPT model to use
    label_num = 8  # the number of dimensions of this variable
    valid_values = ['0', '1']  # the valid answers from this question
    temperature = 0.7  # temperature 
    q_name = "Q3"  # the name of this question/variable
    once_verify_num = 3  # the numbers of results generated from GPT 
    max_verify_retry = 5  # the number of retries if the previous is not converged

    # Prompt setup
prompt =  prompt_Q3

    # Initialize GPT Classifier
gpt_classifier = GPTClassifier()

    # Setup classification task
classification_task = ClassificationTask(
        column=column_name,
        prompt=prompt,
        model_name=model_name,
        label_num=label_num,
        valid_values=valid_values,
        temperature=temperature,
        q_name=q_name,
        once_verify_num=once_verify_num,
        max_verify_retry=max_verify_retry
    )

    # Classify and save the result
classified_df = gpt_classifier.classify_df(filtered_df, classification_task)
classified_df.to_excel("19_Q3_testdf_result.xlsx")



2023-09-19 19:16:21.837 | INFO     | gpt_classify_function:classify_df:175 - Classifying 1/800 Immigration officials target 7-Eleven shops amid Trump crackdown on undocumented migrants
2023-09-19 19:16:22.373 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['1', '0', '0', '0', '0', '1', '0', '0']", "['1', '0', '0', '0', '0', '1', '0', '0']", "['1', '0', '0', '0', '0', '1', '0', '0']"]
2023-09-19 19:16:22.374 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['1', '0', '0', '0', '0', '1', '0', '0'], ['1', '0', '0', '0', '0', '1', '0', '0'], ['1', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 19:16:22.375 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1_0_0_0_0_1_0_0', 3)]
2023-09-19 19:16:22.375 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1_0_0_0_0_1_0_0 for Immigration officials target 7-Eleven shops amid Trump crackdown on undocumented migrants
2023-09-19 19:16:22.379 | INFO     | gpt

2023-09-19 19:16:25.577 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '1', '0', '1', '0', '0'], ['0', '0', '0', '1', '0', '1', '0', '0'], ['0', '0', '0', '1', '0', '1', '0', '0']]
2023-09-19 19:16:25.577 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_1_0_1_0_0', 3)]
2023-09-19 19:16:25.578 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_1_0_1_0_0 for Trump defends vulgar immigrant comments, partly denies them
2023-09-19 19:16:25.581 | INFO     | gpt_classify_function:classify_df:175 - Classifying 8/800 Fake Highway Signs Jab at New California Immigration Law
2023-09-19 19:16:26.115 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '0', '1', '0']", "['0', '0', '0', '0', '0', '0', '1', '0']", "['0', '0', '0', '0', '0', '0', '1', '0']"]
2023-09-19 19:16:26.116 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0

2023-09-19 19:16:29.391 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '0', '1', '0']", "['0', '0', '0', '0', '0', '0', '1', '0']", "['0', '0', '0', '0', '0', '0', '1', '0']"]
2023-09-19 19:16:29.392 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '0', '1', '0'], ['0', '0', '0', '0', '0', '0', '1', '0'], ['0', '0', '0', '0', '0', '0', '1', '0']]
2023-09-19 19:16:29.393 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_0_1_0', 3)]
2023-09-19 19:16:29.393 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_0_1_0 for Mayors ask administration to extend immigration program for El Salvador
2023-09-19 19:16:29.396 | INFO     | gpt_classify_function:classify_df:175 - Classifying 15/800 DHS Checks 100 7-Eleven Stores for Immigration Fraud
2023-09-19 19:16:29.946 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['1',

2023-09-19 19:16:32.878 | INFO     | gpt_classify_function:classify_df:175 - Classifying 21/800 Trump Immigration Plan Angers Both Sides; Source: Trump Tried to Fire Robert Mueller; Interview with Virginia Senator Mark Warner; Don McGahn, a Key Player in Multiple White House Controversies. Aired 4-4:30p ET
2023-09-19 19:16:33.416 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '1', '1', '0']", "['0', '0', '0', '0', '0', '1', '1', '0']", "['0', '0', '0', '0', '0', '1', '1', '0']"]
2023-09-19 19:16:33.417 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0']]
2023-09-19 19:16:33.418 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_1_0', 3)]
2023-09-19 19:16:33.418 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_1_0 for Trump I

2023-09-19 19:16:36.567 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '1', '0', '1', '0', '0']", "['0', '0', '0', '1', '0', '1', '0', '0']", "['0', '0', '0', '1', '0', '1', '0', '0']"]
2023-09-19 19:16:36.568 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '1', '0', '1', '0', '0'], ['0', '0', '0', '1', '0', '1', '0', '0'], ['0', '0', '0', '1', '0', '1', '0', '0']]
2023-09-19 19:16:36.569 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_1_0_1_0_0', 3)]
2023-09-19 19:16:36.569 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_1_0_1_0_0 for Rand Paul: We Can’t Do Immigration Reform ‘If Everybody’s Out There Calling’ Trump a ‘Racist’
2023-09-19 19:16:36.572 | INFO     | gpt_classify_function:classify_df:175 - Classifying 29/800 Border inspections of electronic devices hits record high
2023-09-19 19:16:37.073 | DEBUG    | gpt_classify_function:classify

...

2023-09-19 19:23:33.004 | INFO     | gpt_classify_function:classify_df:175 - Classifying 769/800 ‘Conservative’ NYT Columnists Have A Habit Of Telling Americans They’re Worse Than Immigrants
2023-09-19 19:23:33.523 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '1', '0', '0', '0', '0']", "['0', '0', '0', '1', '0', '0', '0', '0']", "['0', '0', '0', '1', '0', '0', '0', '0']"]
2023-09-19 19:23:33.524 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '1', '0', '0', '0', '0'], ['0', '0', '0', '1', '0', '0', '0', '0'], ['0', '0', '0', '1', '0', '0', '0', '0']]
2023-09-19 19:23:33.524 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_1_0_0_0_0', 3)]
2023-09-19 19:23:33.525 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_1_0_0_0_0 for ‘Conservative’ NYT Columnists Have A Habit Of Telling Americans They’re Worse Than Immigrants
2023-09-19 19:23:33.528 | INFO

2023-09-19 19:23:36.670 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_0_0_1_0_0', 3)]
2023-09-19 19:23:36.670 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_0_0_1_0_0 for Warren Hits Trump on Immigration: 'Dreamers Aren't Bargaining Chips'
2023-09-19 19:23:36.673 | INFO     | gpt_classify_function:classify_df:175 - Classifying 776/800 Analysis: Trump tries to deal, prove mental stability at televised immigration meeting
2023-09-19 19:23:37.214 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '1', '0', '0']", "['0', '0', '0', '0', '0', '1', '0', '0']", "['0', '0', '0', '0', '0', '1', '0', '0']"]
2023-09-19 19:23:37.215 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0'], ['0', '0', '0', '0', '0', '1', '0', '0']]
2023-09-19 19:23:37.216 | INFO     | gpt_classify_function:mul

2023-09-19 19:23:40.442 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '1', '0', '1', '0', '0']", "['0', '0', '0', '1', '0', '1', '0', '0']", "['0', '0', '0', '1', '0', '1', '0', '0']"]
2023-09-19 19:23:40.443 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '1', '0', '1', '0', '0'], ['0', '0', '0', '1', '0', '1', '0', '0'], ['0', '0', '0', '1', '0', '1', '0', '0']]
2023-09-19 19:23:40.444 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_0_0_1_0_1_0_0', 3)]
2023-09-19 19:23:40.444 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_0_0_1_0_1_0_0 for Nicolle Wallace: Trump 'speaks in a racist way about Haitians'
2023-09-19 19:23:40.447 | INFO     | gpt_classify_function:classify_df:175 - Classifying 784/800 N.Y. City Councilmen Arrested as Immigrant Rights Leader Is Detained
2023-09-19 19:23:40.967 | DEBUG    | gpt_classify_function:classify:119 - Raw results:

2023-09-19 19:23:43.695 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('0_1_0_0_0_0_0_0', 3)]
2023-09-19 19:23:43.696 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 0_1_0_0_0_0_0_0 for Motel 6 Gave Guest Info To Immigration Agents, Washington State Attorney General Alleges
2023-09-19 19:23:43.701 | INFO     | gpt_classify_function:classify_df:175 - Classifying 791/800 Trump Is Right: Giving Priority To 'The Wall' Is For The Good Of All
2023-09-19 19:23:44.210 | DEBUG    | gpt_classify_function:classify:119 - Raw results: ["['0', '0', '0', '0', '0', '1', '1', '0']", "['0', '0', '0', '0', '0', '1', '1', '0']", "['0', '0', '0', '0', '0', '1', '1', '0']"]
2023-09-19 19:23:44.210 | DEBUG    | gpt_classify_function:classify:139 - Valid results: [['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0'], ['0', '0', '0', '0', '0', '1', '1', '0']]
2023-09-19 19:23:44.211 | INFO     | gpt_classify_function:m

2023-09-19 19:23:46.819 | INFO     | gpt_classify_function:multi_verify:159 - Try:1 Sorted classifications: [('1_0_0_0_0_0_0_0', 3)]
2023-09-19 19:23:46.819 | SUCCESS  | gpt_classify_function:multi_verify:161 - Try:1 Verified as 1_0_0_0_0_0_0_0 for Immigration agents hit this popular business hard looking for illegal workers
2023-09-19 19:23:46.822 | INFO     | gpt_classify_function:classify_df:175 - Classifying 799/800 Trump Suggests Comprehensive Immigration Reform If He Gets His Border Wall
2023-09-19 19:23:46.825 | INFO     | gpt_classify_function:multi_verify:144 - Cache hit ['0', '0', '0', '0', '0', '1', '1', '0'] Trump Suggests Comprehensive Immigration Reform If He Gets His Border Wall
2023-09-19 19:23:46.825 | INFO     | gpt_classify_function:classify_df:175 - Classifying 800/800 Establishment Media Rally for Chain Migration by Attacking Trump Advisers’ Family History of Legally Entering U.S.
2023-09-19 19:23:47.339 | DEBUG    | gpt_classify_function:classify:119 - Raw results

In [78]:
# check if any colomn has error or can not converge after the max_verify_retry that needs human validation
review_human_validation_rows(df=classified_df, text_column="Post_Title", 
                                        valid_values= ['0', '1'] ,  
                                        classification_columns=['Q3_1', 'Q3_2','Q3_3', 'Q3_4', 'Q3_5', 'Q3_6','Q3_7', 'Q3_8'])


No row needs human validation, please proceed


ID  ID_original                                  GUID  \
0     302         1504  8427d7da-077d-4557-b1f5-987abf8a10a5   
1     756         3710  2f2e22e4-20db-40e7-a877-ca574d1ba7b5   
2    1614         7442  c03828e7-e53c-47b7-9bdb-b4c33820854e   
3    1329         6144  790ad6df-bc2c-4199-9985-1258491e4f44   
4    1477         6830  59747e7c-fba0-4d85-9d51-094168531e32   
..    ...          ...                                   ...   
795  1493         6882  b1412373-4338-4fdd-921a-dd1eb36285e1   
796   239         1147  453966ad-dbcf-43b6-82c3-44795077fa29   
797   514         2524  ebe0feb9-a8e9-4fd6-bd8d-3e57de1fe0fd   
798  1182         5567  a7803b28-642f-4624-aab8-ce81d14a0a4d   
799  1906           17  64a7153b-cdcd-49fd-a3d5-d131c876ed28   

             Date (GMT)                                                URL  \
0   2018-01-11 23:48:07  https://www.yahoo.com/news/immigration-officia...   
1   2018-01-05 17:40:14  http://www.foxnews.com/us/2018/01/05/illegal-i...   
2   2018-01-07 21:25:50  https://www.yahoo.com/news/m/de1c6a57-6822-3e5...   
3   2018-01-09 12:24:44  http://www.cnn.com/transcripts/1801/08/ath.02....   
4   2018-01-14 22:47:56  https://www.dailykos.com/stories/2018/1/14/173...   
..                  ...                                                ...   
795 2018-01-08 21:57:16  http://www.motherjones.com/kevin-drum/2018/01/...   
796 2018-01-10 05:58:06  http://abcnews.go.com/International/wireStory/...   
797 2018-01-11 00:57:11  http://www.theblaze.com/news/2018/01/10/immigr...   
798 2018-01-10 09:07:51  https://www.yahoo.com/news/trump-suggests-comp...   
799 2018-02-08 23:17:31  http://www.breitbart.com/big-government/2018/0...   

                                            Post_Title Q1  Q2  Q3_1_og  \
0    Immigration officials target 7-Eleven shops am...  1   2      1.0   
1    Illegal immigrant who killed Kate Steinle like...  1   1      2.0   
2    Trump, seeking $18B for border wall, ties proj...  1   2      6.0   
3    Trump: Congress Must Fund Border Wall for DACA...  2  99     99.0   
4    Donald Trump this past Tuesday held a bipartis...  1   2      6.0   
..                                                 ... ..  ..      ...   
795  Donald Trump Wants to Waste a Lot of Money on ...  1   2      6.0   
796  The Latest: Feds object to judge's immigration...  1   2     99.0   
797  Immigration agents hit this popular business h...  1   2      1.0   
798  Trump Suggests Comprehensive Immigration Refor...  1   2      6.0   
799  Establishment Media Rally for Chain Migration ...  1   2      6.0   

     Q3_2_og  ... accurate Q2_1_classification Q3_1_classification  \
0        2.0  ...    False                   1                   1   
1       99.0  ...     True                   1                   0   
2        1.0  ...     True                   2                   1   
3       99.0  ...    False                   1                   0   
4        7.0  ...     True                   2                   0   
..       ...  ...      ...                 ...                 ...   
795      1.0  ...     True                   2                   1   
796     99.0  ...    False                   1                   0   
797     99.0  ...    False                   1                   1   
798     99.0  ...     True                   2                   0   
799     99.0  ...     True                   2                   0   

    Q3_2_classification Q3_3_classification Q3_4_classification  \
0                     0                   0                   0   
1                     1                   0                   0   
2                     0                   0                   0   
3                     0                   0                   0   
4                     0                   0                   0   
..                  ...                 ...                 ...   
795                   0                   0                   0   
796                   0            

In [89]:
# Merge the result to test_df and enter "0" for the rows that Q1_1_classification= "2"
 # Step 1: Create new columns named Q3_1_classification to Q3_8_classification in test_df
for i in range(1, 9):
    col_name = f'Q3_{i}_classification'
    test_df[col_name] = None

# Step 2: Copy values from classified_df to test_df based on matching ID_original values
for idx, row in test_df.iterrows():
    matching_row = classified_df[classified_df['GUID'] == row['GUID']]
    if not matching_row.empty:
        for i in range(1, 9):
            col_name = f'Q3_{i}_classification'
            test_df.at[idx, col_name] = matching_row[col_name].iloc[0]

# Step 3: Set Q3_1_classification to Q3_8_classification to "99" where Q1_1_classification is "2"
for i in range(1, 9):
    col_name = f'Q3_{i}_classification'
    test_df.loc[test_df['Q1_1_classification'] != "1", col_name] = "0"

test_df.to_excel("20_Q3_testdf_result_whole.xlsx")


In [93]:
# caculate accuarcy for test df in which Q1 == 1
accuracies = {}

for i in range(1, 9):  # Loop from 2 to 8
    predict_col = f"Q3_{i}_classification"
    actual_col = f"Q3_{i}"
    
    accuracy = compute_accuracy(df=classified_df, 
                                predict_cols=[predict_col], 
                                actual_cols=[actual_col])
    
    accuracies[actual_col] = accuracy

# Print the accuracies
for col, acc in accuracies.items():
    print(f"Accuracy for {col}: {acc}")


Accuracy for Q3_1: 0.96625
Accuracy for Q3_2: 0.9525
Accuracy for Q3_3: 0.9875
Accuracy for Q3_4: 0.87125
Accuracy for Q3_5: 0.97625
Accuracy for Q3_6: 0.93375
Accuracy for Q3_7: 0.8675
Accuracy for Q3_8: 0.94375


In [94]:
# caculate accuarcy for whole test df
accuracies = {}

for i in range(1, 9):  # Loop from 2 to 8
    predict_col = f"Q3_{i}_classification"
    actual_col = f"Q3_{i}"
    
    accuracy = compute_accuracy(df=test_df, 
                                predict_cols=[predict_col], 
                                actual_cols=[actual_col])
    
    accuracies[actual_col] = accuracy

# Print the accuracies
print("Here's the accuracy for the Q3 for the test df:")
for col, acc in accuracies.items():
    print(f"Accuracy for {col}: {acc}")


Here's the accuracy for the Q3 for the test df:
Accuracy for Q3_1: 0.973026973026973
Accuracy for Q3_2: 0.958041958041958
Accuracy for Q3_3: 0.99000999000999
Accuracy for Q3_4: 0.8911088911088911
Accuracy for Q3_5: 0.98001998001998
Accuracy for Q3_6: 0.9400599400599401
Accuracy for Q3_7: 0.8931068931068931
Accuracy for Q3_8: 0.954045954045954
